In [ ]:
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split

from numpy import mean
from numpy import std

from matplotlib import pyplot
from sklearn.metrics import accuracy_score,confusion_matrix,classification_report
from sklearn.preprocessing import QuantileTransformer
from sklearn.pipeline import Pipeline

from scipy.stats import mode

In [ ]:
!nvidia-smi  

Sun May 22 00:38:50 2022       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 460.32.03    Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla V100-SXM2...  Off  | 00000000:00:04.0 Off |                    0 |
| N/A   33C    P0    24W / 300W |      0MiB / 16160MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [ ]:
from pydrive.auth import GoogleAuth
from pydrive.drive import GoogleDrive
from google.colab import auth
from oauth2client.client import GoogleCredentials

In [ ]:
auth.authenticate_user()
gauth = GoogleAuth()
gauth.credentials = GoogleCredentials.get_application_default()
drive = GoogleDrive(gauth)

In [ ]:
#npz files can only be loaded using /gdrive path
from google.colab import drive
drive.mount('/content/gdrive')
#%cd /gdrive

Mounted at /content/gdrive


In [ ]:
!pip install mne

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 7.5 MB 14.2 MB/s 


In [ ]:
#import pyeeg
from tensorflow import keras 

In [ ]:
%matplotlib inline

import glob
import math
import ntpath
import random, os, sys
import numpy as np
import pandas as pd
import tensorflow as tf
import matplotlib.pyplot as plt
import seaborn as sns
#import edfreader
#import models
import mne
#import pyeeg
import warnings
warnings.filterwarnings('ignore')

from matplotlib.backends.backend_pdf import PdfPages
from mne.datasets.sleep_physionet._utils import _fetch_one, _data_path, AGE_SLEEP_RECORDS, _check_subjects
from datetime import datetime
from mne import Epochs, pick_types, find_events
from mne.io import concatenate_raws, read_raw_edf
from mne.time_frequency import psd_welch
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import classification_report

from tqdm.notebook import tqdm
from sklearn.model_selection import train_test_split
from tensorflow import keras

from tensorflow.keras.utils import to_categorical

from tensorflow.keras.callbacks import ModelCheckpoint, ReduceLROnPlateau, CSVLogger
import imblearn
from imblearn.over_sampling import SMOTE
from sklearn.svm import SVC
import joblib

from sklearn.metrics import make_scorer, f1_score, accuracy_score, classification_report, log_loss
from sklearn.metrics import roc_auc_score, confusion_matrix, roc_auc_score, roc_curve

from sklearn.tree import DecisionTreeClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier, AdaBoostClassifier, GradientBoostingClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.discriminant_analysis import QuadraticDiscriminantAnalysis
#from xgboost import XGBClassifier
#import xgboost

In [ ]:
VBS = True  # constant boolean to enable/disbale verbose
EPOCH_SEC_SIZE = 30  # Epoch duration selection
seed = 42  # seed value for the random seeds
batch_size = 64
number_of_files = 100 #100 npz files, 50 subjects, each suject has 2 nights, so 2 files per subject (50*2)=100

# values to label the stages
UNKNOWN = -1
W = 0
N1 = 1
N2 = 2
N3 = 3
REM = 4

# making string dictionary for the label values
label_dict = {
    "UNKNOWN"  : UNKNOWN,
    "W"        : W,
    "N1"       : N1,
    "N2"       : N2,
    "N3"       : N3,
    "REM"      : REM
}

# converting from label values to strings 
class_dict = {
    -1: "UNKNOWN",
    0 : "W",
    1 : "N1",
    2 : "N2",
    3 : "N3",
    4 : "REM"
}

# annotation dictionary to convert from string to label values
annot2label = {
    "Sleep stage ?": -1,
    "Movement time": -1,
    "Sleep stage W": 0,
    "Sleep stage 1": 1,
    "Sleep stage 2": 2,
    "Sleep stage 3": 3,
    "Sleep stage 4": 3,
    "Sleep stage R": 4
}
#project_path = os.path.abspath(os.getcwd())  # finding the current project path in windows

In [ ]:
from tensorflow.keras import optimizers, losses, activations, models
from tensorflow.keras.models import Model, load_model
from tensorflow.keras.layers import GlobalMaxPool1D, GlobalAveragePooling1D, concatenate, SpatialDropout1D, TimeDistributed, Bidirectional, LSTM
from tensorflow.keras.layers import Input, Conv1D, Dense, Dropout, MaxPool1D, Activation
from tensorflow.keras.layers import Reshape, LSTM, TimeDistributed, Bidirectional, BatchNormalization, Flatten, RepeatVector
from tensorflow.keras.optimizers import Adam
#from keras_contrib.layers import CRF

from scipy.signal import butter, lfilter


In [ ]:
Fs = 100
from keras.utils import np_utils

In [ ]:
subject_481_df=pd.read_csv('/content/gdrive/My Drive/physionet/ensemble/50_subs/subject_481_dataset.csv',header=None)

In [ ]:
x_sub_set=subject_481_df.drop([3000],axis=1)

In [ ]:
x_sub_set

In [ ]:
y_sub_dt=subject_481_df[3000]

In [ ]:
y_sub_dt

In [ ]:
x_train_sub,x_test_sub,y_train_sub,y_test_sub=train_test_split(x_sub_set,y_sub_dt,test_size=0.2,random_state=100)

In [ ]:
pip install git+https://www.github.com/keras-team/keras-contrib.git

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Cloning https://www.github.com/keras-team/keras-contrib.git to /tmp/pip-req-build-3e59emfe
  Running command git clone -q https://www.github.com/keras-team/keras-contrib.git /tmp/pip-req-build-3e59emfe
  Created wheel for keras-contrib: filename=keras_contrib-2.0.8-py3-none-any.whl size=101077 sha256=78eeae0a85666872e5faecebeef3bfa88e9367eff87a94a6d70878ae4a1ab269
  Stored in directory: /tmp/pip-ephem-wheel-cache-v5te5zac/wheels/bb/1f/f2/b57495012683b6b20bbae94a3915ec79753111452d79886abc
Successfully built keras-contrib


In [ ]:
from keras import optimizers, losses, activations, models
from keras.layers import Dense, Input, Dropout, Convolution1D, MaxPool1D, GlobalMaxPool1D, GlobalAveragePooling1D, concatenate, SpatialDropout1D, TimeDistributed, Bidirectional, LSTM
from keras_contrib.layers import CRF

WINDOW_SIZE = 100

optimizer = Adam(lr=1e-4)

from scipy.stats import mode

In [ ]:
nclass = 5

#n_classes=5
def model_b(n_classes=5, use_sub_layer=False, use_rnn=True, verbose=False):
    inputLayer = Input(shape=(3000, 1), name='inLayer')
    convFine = Conv1D(filters=64, kernel_size=int(Fs/2), strides=int(Fs/16), padding='same', activation='relu', name='fConv1')(inputLayer)
    convFine = MaxPool1D(pool_size=8, strides=8, name='fMaxP1')(convFine)
    convFine = Dropout(rate=0.5, name='fDrop1')(convFine)
    convFine = Conv1D(filters=128, kernel_size=8, padding='same', activation='relu', name='fConv2')(convFine)
    convFine = Conv1D(filters=128, kernel_size=8, padding='same', activation='relu', name='fConv3')(convFine)
    convFine = Conv1D(filters=128, kernel_size=8, padding='same', activation='relu', name='fConv4')(convFine)
    convFine = MaxPool1D(pool_size=4, strides=4, name='fMaxP2')(convFine)
    fineShape = convFine.get_shape()
    convFine = Flatten(name='fFlat1')(convFine)
    
    # network to learn coarse features
    convCoarse = Conv1D(filters=32, kernel_size=Fs*4, strides=int(Fs/2), padding='same', activation='relu', name='cConv1')(inputLayer)
    convCoarse = MaxPool1D(pool_size=4, strides=4, name='cMaxP1')(convCoarse)
    convCoarse = Dropout(rate=0.5, name='cDrop1')(convCoarse)
    convCoarse = Conv1D(filters=128, kernel_size=6, padding='same', activation='relu', name='cConv2')(convCoarse)
    convCoarse = Conv1D(filters=128, kernel_size=6, padding='same', activation='relu', name='cConv3')(convCoarse)
    convCoarse = Conv1D(filters=128, kernel_size=6, padding='same', activation='relu', name='cConv4')(convCoarse)
    convCoarse = MaxPool1D(pool_size=2, strides=2, name='cMaxP2')(convCoarse)
    coarseShape = convCoarse.get_shape()
    convCoarse = Flatten(name='cFlat1')(convCoarse)
    
    # concatenate coarse and fine cnns
    mergeLayer = concatenate([convFine, convCoarse], name='merge_1')
    outLayer = Dropout(rate=0.5, name='mDrop1')(mergeLayer)
    
    outLayer = Reshape((1, outLayer.get_shape()[1]), name='reshape1')(outLayer)
    outLayer = LSTM(64, return_sequences=True)(outLayer)
    outLayer = LSTM(64, return_sequences=False)(outLayer)

    # Classify
    outLayer = Dense(n_classes, activation='softmax', name='outLayer')(outLayer)
    model = Model(inputLayer, outLayer)
    optimizer = Adam(lr=1e-4)
    model.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['acc'])
    #model.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['accuracy'])
    if verbose:
        model.summary()
    return model

In [ ]:
loaded_model_shuf1=model_b(verbose=VBS)
loaded_model_shuf2=model_b(verbose=VBS)
loaded_model_shuf3=model_b(verbose=VBS)

Model: "model"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 inLayer (InputLayer)           [(None, 3000, 1)]    0           []                               
                                                                                                  
 fConv1 (Conv1D)                (None, 500, 64)      3264        ['inLayer[0][0]']                
                                                                                                  
 cConv1 (Conv1D)                (None, 60, 32)       12832       ['inLayer[0][0]']                
                                                                                                  
 fMaxP1 (MaxPooling1D)          (None, 62, 64)       0           ['fConv1[0][0]']                 
                                                                                              

In [ ]:
#dt_shuf1
checkpoint_path_load_model_30_epochs_shuf1 = "/content/gdrive/My Drive/physionet/dt_shuf1_phy/sub_482_75th_sub_with_50_sub_tr_dt/weights-phy_shuf1_30_epochs.ckpt"
checkpoint_load_model_30_epochs_shuf1_dir = os.path.dirname(checkpoint_path_load_model_30_epochs_shuf1)
#latest_30_epochs_shuf1_s828=tensorflow.train.latest_checkpoint(checkpoint_load_model_300_epochs_shuf1_s828_dir)
print(checkpoint_path_load_model_30_epochs_shuf1)

/content/gdrive/My Drive/physionet/dt_shuf1_phy/sub_482_75th_sub_with_50_sub_tr_dt/weights-phy_shuf1_30_epochs.ckpt


In [ ]:
#dt_shuf2
checkpoint_path_load_model_30_epochs_shuf2 = "/content/gdrive/My Drive/physionet/dt_shuf2_phy/sub_482_75th_sub_with_50_sub_tr_dt/weights-phy_shuf2_30_epochs.ckpt"
checkpoint_load_model_30_epochs_shuf2_dir = os.path.dirname(checkpoint_path_load_model_30_epochs_shuf2)
#latest_300_epochs_shuf2_s828=tensorflow.train.latest_checkpoint(checkpoint_load_model_300_epochs_shuf2_s828_dir)
print(checkpoint_path_load_model_30_epochs_shuf2)

/content/gdrive/My Drive/physionet/dt_shuf2_phy/sub_482_75th_sub_with_50_sub_tr_dt/weights-phy_shuf2_30_epochs.ckpt


In [ ]:
#dt_shuf3
checkpoint_path_load_model_30_epochs_shuf3 = "/content/gdrive/My Drive/physionet/dt_shuf3_phy/sub_482_75th_sub_with_50_sub_tr_dt/weights-phy_shuf3_30_epochs.ckpt"
checkpoint_load_model_30_epochs_shuf3_dir = os.path.dirname(checkpoint_path_load_model_30_epochs_shuf3)
#latest_300_epochs_shuf3_s828=tensorflow.train.latest_checkpoint(checkpoint_load_model_300_epochs_shuf3_s828_dir)
print(checkpoint_path_load_model_30_epochs_shuf3)

/content/gdrive/My Drive/physionet/dt_shuf3_phy/sub_482_75th_sub_with_50_sub_tr_dt/weights-phy_shuf3_30_epochs.ckpt


In [ ]:
loaded_model_shuf1.load_weights(checkpoint_path_load_model_30_epochs_shuf1)
loaded_model_shuf2.load_weights(checkpoint_path_load_model_30_epochs_shuf2)
loaded_model_shuf3.load_weights(checkpoint_path_load_model_30_epochs_shuf3)

In [ ]:
for i,layer in enumerate(loaded_model_shuf1.layers):
  print(i,layer.name)

0 inLayer
1 fConv1
2 cConv1
3 fMaxP1
4 cMaxP1
5 fDrop1
6 cDrop1
7 fConv2
8 cConv2
9 fConv3
10 cConv3
11 fConv4
12 cConv4
13 fMaxP2
14 cMaxP2
15 fFlat1
16 cFlat1
17 merge_1
18 mDrop1
19 reshape1
20 lstm
21 lstm_1
22 outLayer


In [ ]:
for i,layer in enumerate(loaded_model_shuf1.layers):
  print(i,layer.name,layer.trainable)

0 inLayer True
1 fConv1 True
2 cConv1 True
3 fMaxP1 True
4 cMaxP1 True
5 fDrop1 True
6 cDrop1 True
7 fConv2 True
8 cConv2 True
9 fConv3 True
10 cConv3 True
11 fConv4 True
12 cConv4 True
13 fMaxP2 True
14 cMaxP2 True
15 fFlat1 True
16 cFlat1 True
17 merge_1 True
18 mDrop1 True
19 reshape1 True
20 lstm True
21 lstm_1 True
22 outLayer True


In [ ]:
for layer in loaded_model_shuf1.layers[:23]:
  layer.trainable=False
#for layer in loaded_model_shuf1.layers[20:]:
 # layer.trainable=False

In [ ]:
for i,layer in enumerate(loaded_model_shuf1.layers):
  print(i,layer.name,layer.trainable)

0 inLayer False
1 fConv1 False
2 cConv1 False
3 fMaxP1 False
4 cMaxP1 False
5 fDrop1 False
6 cDrop1 False
7 fConv2 False
8 cConv2 False
9 fConv3 False
10 cConv3 False
11 fConv4 False
12 cConv4 False
13 fMaxP2 False
14 cMaxP2 False
15 fFlat1 False
16 cFlat1 False
17 merge_1 False
18 mDrop1 False
19 reshape1 False
20 lstm False
21 lstm_1 False
22 outLayer False


In [ ]:
for layer in loaded_model_shuf2.layers[:23]:
  layer.trainable=False
#for layer in loaded_model_shuf2.layers[20:]:
 # layer.trainable=False

In [ ]:
for layer in loaded_model_shuf3.layers[:23]:
  layer.trainable=False
#for layer in loaded_model_shuf3.layers[20:]:
#  layer.trainable=False

In [ ]:
for i,layer in enumerate(loaded_model_shuf2.layers):
  print(i,layer.name,layer.trainable)

0 inLayer False
1 fConv1 False
2 cConv1 False
3 fMaxP1 False
4 cMaxP1 False
5 fDrop1 False
6 cDrop1 False
7 fConv2 False
8 cConv2 False
9 fConv3 False
10 cConv3 False
11 fConv4 False
12 cConv4 False
13 fMaxP2 False
14 cMaxP2 False
15 fFlat1 False
16 cFlat1 False
17 merge_1 False
18 mDrop1 False
19 reshape1 False
20 lstm_2 False
21 lstm_3 False
22 outLayer False


In [ ]:
for i,layer in enumerate(loaded_model_shuf3.layers):
  print(i,layer.name,layer.trainable)

0 inLayer False
1 fConv1 False
2 cConv1 False
3 fMaxP1 False
4 cMaxP1 False
5 fDrop1 False
6 cDrop1 False
7 fConv2 False
8 cConv2 False
9 fConv3 False
10 cConv3 False
11 fConv4 False
12 cConv4 False
13 fMaxP2 False
14 cMaxP2 False
15 fFlat1 False
16 cFlat1 False
17 merge_1 False
18 mDrop1 False
19 reshape1 False
20 lstm_4 False
21 lstm_5 False
22 outLayer False


In [ ]:
loaded_model_shuf1.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['accuracy'])
loaded_model_shuf2.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['accuracy'])
loaded_model_shuf3.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['accuracy'])

In [ ]:
print(loaded_model_shuf1.summary())
print(loaded_model_shuf2.summary())
print(loaded_model_shuf3.summary())

Model: "model"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 inLayer (InputLayer)           [(None, 3000, 1)]    0           []                               
                                                                                                  
 fConv1 (Conv1D)                (None, 500, 64)      3264        ['inLayer[0][0]']                
                                                                                                  
 cConv1 (Conv1D)                (None, 60, 32)       12832       ['inLayer[0][0]']                
                                                                                                  
 fMaxP1 (MaxPooling1D)          (None, 62, 64)       0           ['fConv1[0][0]']                 
                                                                                              

In [ ]:
x_train_sub.shape

In [ ]:
x_train_sub

0         1         2     ...      2997      2998      2999
774  -0.037317 -0.035184 -0.053523  ... -0.056081 -0.107685 -0.138817
2812  0.022085 -0.017796 -0.064110  ... -0.084265 -0.057249 -0.053389
2615 -0.127577 -0.109566 -0.066254  ...  0.021656  0.037094  0.021656
2706 -0.147303 -0.149447 -0.105278  ...  0.111710  0.105278  0.122860
1479 -0.071861 -0.088920 -0.128156  ... -0.012581 -0.015140  0.001919
...        ...       ...       ...  ...       ...       ...       ...
1930 -0.002359  0.139156 -0.008791  ... -0.048672 -0.414036 -0.345852
79   -0.136259 -0.109391 -0.123891  ... -0.052243 -0.233495 -0.170376
1859  0.016081  0.049101 -0.076117  ... -0.027231  0.014366 -0.018225
2840 -0.009220 -0.006647 -0.006218  ...  0.073544  0.057678  0.033663
1544  0.007890 -0.079964 -0.121332  ...  0.136685  0.148626  0.104273

[2456 rows x 3000 columns]

In [ ]:
tf.config.run_functions_eagerly(True)

In [ ]:
x_train_sub[0:500]

In [ ]:
x_test_sub.shape

In [ ]:
train_dt=x_train_sub
train_dt['sleep_stage']=y_train_sub

In [ ]:
test_dt=x_test_sub
test_dt['sleep_stage']=y_test_sub

In [ ]:
train_dt.shape

In [ ]:
test_dt.shape

In [ ]:
test_dt.to_csv(r'/content/gdrive/My Drive/physionet/ensemble/50_subs/x_test_sub.csv', header=False, index=False)

In [ ]:
train_dt.to_csv(r'/content/gdrive/My Drive/physionet/ensemble/50_subs/x_train_sub.csv', header=False, index=False)

In [ ]:
tr_dt=pd.read_csv('/content/gdrive/My Drive/physionet/ensemble/50_subs/x_train_sub.csv', header=None)

In [ ]:
tr_dt

0         1         2         3         4         5         6     \
0     0.008521 -0.021337 -0.023599 -0.011384 -0.005051  0.006259  0.029784   
1     0.036570  0.025712  0.022093  0.026617  0.027974 -0.013194 -0.069290   
2     0.029801  0.029351  0.076605 -0.003951  0.022151  0.047353  0.165262   
3     0.047427  0.085428  0.082714  0.083166  0.094476  0.084523  0.072309   
4     0.416383  0.437534  0.459136  0.460486  0.450135  0.424033  0.438884   
...        ...       ...       ...       ...       ...       ...       ...   
1975  0.003997  0.004450  0.019831  0.028427  0.027974  0.005354 -0.015456   
1976 -0.057506 -0.007102  0.013150  0.029351  0.032502  0.050503  0.029351   
1977 -0.043052 -0.035361 -0.011384 -0.004146 -0.014551 -0.032194 -0.029027   
1978 -0.006202 -0.000351  0.003699 -0.012502 -0.079557 -0.057506  0.011350   
1979  0.034302  0.052303  0.067604  0.098207  0.108558  0.082456  0.030251   

          7         8         9     ...      2991      2992      2993  \
0     0.019831  0.020283  0.036570  ... -0.061147 -0.065219 -0.065671   
1    -0.087838 -0.075171 -0.038075  ...  0.035665 -0.002336 -0.024503   
2    -0.051205  0.033402  0.034752  ... -0.077307 -0.083158 -0.055256   
3     0.045165  0.022998  0.009878  ... -0.087838 -0.101863 -0.108648   
4     0.481638  0.511340  0.514041  ... -0.035454 -0.004401 -0.003501   
...        ...       ...       ...  ...       ...       ...       ...   
1975 -0.011384  0.017117  0.010783  ...  0.001735 -0.032194 -0.073814   
1976  0.045103  0.082906  0.074355  ...  0.189114  0.132410  0.136010   
1977 -0.030837 -0.040790 -0.036266  ...  0.037474  0.008069 -0.022694   
1978 -0.030053 -0.048955  0.048253  ...  0.025751  0.022151  0.038802   
1979  0.036102  0.032502  0.010450  ...  0.125209  0.084706  0.076605   

          2994      2995      2996      2997      2998      2999  3000  
0    -0.072457 -0.076529 -0.066124 -0.045766 -0.029027 -0.038528     4  
1    -0.052099 -0.042599 -0.019527 -0.012289  0.003545  0.006259     1  
2    -0.005752  0.001449 -0.024203 -0.005752 -0.037704 -0.065156     0  
3    -0.117244 -0.102315 -0.087386 -0.079695 -0.070195 -0.051647     4  
4    -0.009352  0.010450  0.022151  0.038802  0.040152  0.070305     2  
...        ...       ...       ...       ...       ...       ...   ...  
1975 -0.102315 -0.091005 -0.076076 -0.055719 -0.005955  0.046522     4  
1976  0.131060  0.136010  0.144561  0.173813  0.172463  0.131510     2  
1977 -0.051647 -0.032646 -0.035361 -0.037623 -0.055719 -0.073814     2  
1978  0.039252  0.010900  0.013600 -0.029603 -0.034104 -0.066056     0  
1979  0.090556  0.115308  0.112158  0.166162  0.251219  0.302973     2  

[1980 rows x 3001 columns]

In [ ]:
x_sub_set=tr_dt.drop([3000],axis=1)
y_sub_dt=tr_dt[3000]

In [ ]:
loaded_model_shuf1_new=model_b(verbose=VBS)
loaded_model_shuf2_new=model_b(verbose=VBS)
loaded_model_shuf3_new=model_b(verbose=VBS)

Model: "model_3"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 inLayer (InputLayer)           [(None, 3000, 1)]    0           []                               
                                                                                                  
 fConv1 (Conv1D)                (None, 500, 64)      3264        ['inLayer[0][0]']                
                                                                                                  
 cConv1 (Conv1D)                (None, 60, 32)       12832       ['inLayer[0][0]']                
                                                                                                  
 fMaxP1 (MaxPooling1D)          (None, 62, 64)       0           ['fConv1[0][0]']                 
                                                                                            

In [ ]:
loaded_model_shuf1_new.load_weights(checkpoint_path_load_model_30_epochs_shuf1)
loaded_model_shuf2_new.load_weights(checkpoint_path_load_model_30_epochs_shuf2)
loaded_model_shuf3_new.load_weights(checkpoint_path_load_model_30_epochs_shuf3)

In [ ]:
for layer in loaded_model_shuf1_new.layers[:20]:
  layer.trainable=False
for layer in loaded_model_shuf1_new.layers[20:]:
  layer.trainable=True

In [ ]:
for layer in loaded_model_shuf2_new.layers[:20]:
  layer.trainable=False
for layer in loaded_model_shuf2_new.layers[20:]:
  layer.trainable=True

In [ ]:
for layer in loaded_model_shuf3_new.layers[:20]:
  layer.trainable=False
for layer in loaded_model_shuf3_new.layers[20:]:
  layer.trainable=True

In [ ]:
loaded_model_shuf1_new.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['accuracy'])
loaded_model_shuf2_new.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['accuracy'])
loaded_model_shuf3_new.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['accuracy'])

In [ ]:
loaded_model_shuf1_new.summary()

Model: "model_3"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 inLayer (InputLayer)           [(None, 3000, 1)]    0           []                               
                                                                                                  
 fConv1 (Conv1D)                (None, 500, 64)      3264        ['inLayer[0][0]']                
                                                                                                  
 cConv1 (Conv1D)                (None, 60, 32)       12832       ['inLayer[0][0]']                
                                                                                                  
 fMaxP1 (MaxPooling1D)          (None, 62, 64)       0           ['fConv1[0][0]']                 
                                                                                            

In [ ]:
loaded_model_shuf2_new.summary()

Model: "model_4"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 inLayer (InputLayer)           [(None, 3000, 1)]    0           []                               
                                                                                                  
 fConv1 (Conv1D)                (None, 500, 64)      3264        ['inLayer[0][0]']                
                                                                                                  
 cConv1 (Conv1D)                (None, 60, 32)       12832       ['inLayer[0][0]']                
                                                                                                  
 fMaxP1 (MaxPooling1D)          (None, 62, 64)       0           ['fConv1[0][0]']                 
                                                                                            

In [ ]:
loaded_model_shuf3_new.summary()

Model: "model_5"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 inLayer (InputLayer)           [(None, 3000, 1)]    0           []                               
                                                                                                  
 fConv1 (Conv1D)                (None, 500, 64)      3264        ['inLayer[0][0]']                
                                                                                                  
 cConv1 (Conv1D)                (None, 60, 32)       12832       ['inLayer[0][0]']                
                                                                                                  
 fMaxP1 (MaxPooling1D)          (None, 62, 64)       0           ['fConv1[0][0]']                 
                                                                                            

##Incremental semi-supervised learning

In [ ]:
checkpoint_path_model_inc_shuf1 = "/content/gdrive/My Drive/physionet/ensemble_inc_semi_sup_learning/model_shuf1/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_inc_shuf1 = os.path.dirname(checkpoint_path_model_inc_shuf1)
cp_callback_model_new_shuf1 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_inc_shuf1,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
checkpoint_path_model_inc_shuf2 = "/content/gdrive/My Drive/physionet/ensemble_inc_semi_sup_learning/model_shuf2/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_inc_shuf2 = os.path.dirname(checkpoint_path_model_inc_shuf2)
cp_callback_model_new_shuf2 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_inc_shuf2,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
checkpoint_path_model_inc_shuf3 = "/content/gdrive/My Drive/physionet/ensemble_inc_semi_sup_learning/model_shuf3/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_inc_shuf3 = os.path.dirname(checkpoint_path_model_inc_shuf3)
cp_callback_model_new_shuf3 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_inc_shuf3,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
preds_shuf1=[]
preds_inc_shuf1=[]
probabilities_shuf1=[]
probabilities_inc_shuf1=[]


count_shuf1=0

preds_shuf2=[]
preds_inc_shuf2=[]
probabilities_shuf2=[]
probabilities_inc_shuf2=[]

count_shuf2=0

preds_shuf3=[]
preds_inc_shuf3=[]
probabilities_shuf3=[]
probabilities_inc_shuf3=[]

count_shuf3=0

m_vote_inc=[]

m_vote=[]

count_status1=0
count_status2=0
count_status3=0

for sple in np.array(x_sub_set[0:2457]):

  sple_rshp=sple.reshape(1,3000,1)

  p1_i=loaded_model_shuf1.predict(sple_rshp)

  p1_i_fin=np.argmax(p1_i,axis=1)

  preds_shuf1.append(np.asscalar(p1_i_fin))

  probabilities_shuf1.append(p1_i) 

  
  
  p1_i_inc=loaded_model_shuf1_new.predict_on_batch(sple_rshp)

  p1_i_inc_fin=np.argmax(p1_i_inc,axis=1)

  
  #count_shuf1+=1

  p2_i=loaded_model_shuf2.predict(sple_rshp)

  p2_i_fin=np.argmax(p2_i,axis=1)

  preds_shuf2.append(np.asscalar(p2_i_fin))

  probabilities_shuf2.append(p2_i)

  
    
  p2_i_inc=loaded_model_shuf2_new.predict_on_batch(sple_rshp)

  p2_i_inc_fin=np.argmax(p2_i_inc,axis=1)

  
  #count_shuf2+=1

  p3_i=loaded_model_shuf3.predict(sple_rshp)

  p3_i_fin=np.argmax(p3_i,axis=1)

  preds_shuf3.append(np.asscalar(p3_i_fin))

  probabilities_shuf3.append(p3_i)

  count_status3+=1

  
  p3_i_inc=loaded_model_shuf3_new.predict_on_batch(sple_rshp)

  p3_i_inc_fin=np.argmax(p3_i_inc,axis=1)


  

  preds_inc_shuf1.append(np.asscalar(p1_i_inc_fin))

  probabilities_inc_shuf1.append(p1_i_inc)


  preds_inc_shuf2.append(np.asscalar(p2_i_inc_fin))

  probabilities_inc_shuf2.append(p2_i_inc)


  preds_inc_shuf3.append(np.asscalar(p3_i_inc_fin))

  probabilities_inc_shuf3.append(p3_i_inc)


  mode_i_inc=mode([np.asscalar(p1_i_inc_fin),np.asscalar(p2_i_inc_fin),np.asscalar(p3_i_inc_fin)])
  m_vote_i_inc=mode_i_inc[0][0]
  m_vote_inc.append(m_vote_i_inc)

  mode_i=mode([np.asscalar(p1_i_fin),np.asscalar(p2_i_fin),np.asscalar(p3_i_fin)])
  m_vote_i=mode_i[0][0]
  m_vote.append(m_vote_i)



  p1_i_inc_fin_=np_utils.to_categorical(np.asscalar(p1_i_inc_fin), num_classes=5)
  p2_i_inc_fin_=np_utils.to_categorical(np.asscalar(p2_i_inc_fin), num_classes=5)
  p3_i_inc_fin_=np_utils.to_categorical(np.asscalar(p3_i_inc_fin), num_classes=5)

  p1_i_inc_fin_.shape=(1,5)
  p2_i_inc_fin_.shape=(1,5)
  p3_i_inc_fin_.shape=(1,5)


  p1_i_fin_=np_utils.to_categorical(np.asscalar(p1_i_fin), num_classes=5)
  p2_i_fin_=np_utils.to_categorical(np.asscalar(p2_i_fin), num_classes=5)
  p3_i_fin_=np_utils.to_categorical(np.asscalar(p3_i_fin), num_classes=5)

  p1_i_fin_.shape=(1,5)
  p2_i_fin_.shape=(1,5)
  p3_i_fin_.shape=(1,5)



  

  if p1_i_inc_fin == p1_i_fin:

   
    
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

    

  if p1_i_inc_fin != p1_i_fin:

    p1_i_inc_fin=p1_i_fin

    p1_i_inc_fin_=np_utils.to_categorical(np.asscalar(p1_i_inc_fin), num_classes=5)

    p1_i_inc_fin_.shape=(1,5)

    
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

   

  
  if p2_i_inc_fin == p2_i_fin:
   
      
    
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

    

  if p2_i_inc_fin != p2_i_fin:

    p2_i_inc_fin=p2_i_fin

    p2_i_inc_fin_=np_utils.to_categorical(np.asscalar(p2_i_inc_fin), num_classes=5)

    p2_i_inc_fin_.shape=(1,5)


        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

    
  

  if p3_i_inc_fin == p3_i_fin:

    
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)

    

  if p3_i_inc_fin != p3_i_fin:

    p3_i_inc_fin=p3_i_fin

    p3_i_inc_fin_=np_utils.to_categorical(np.asscalar(p3_i_inc_fin), num_classes=5)

    p3_i_inc_fin_.shape=(1,5)


    
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)

     


  


In [ ]:
print(m_vote)
print(m_vote_inc)

[2, 2, 4, 2, 2, 0, 0, 2, 2, 2, 3, 3, 0, 4, 0, 3, 2, 0, 2, 0, 4, 0, 0, 4, 0, 0, 0, 2, 4, 2, 0, 2, 4, 2, 0, 0, 4, 2, 1, 2, 3, 0, 2, 2, 0, 3, 0, 0, 2, 2, 2, 4, 2, 2, 4, 0, 0, 0, 0, 0, 4, 3, 0, 0, 1, 0, 2, 2, 0, 0, 2, 0, 2, 2, 0, 0, 0, 2, 0, 0, 2, 1, 2, 2, 0, 0, 0, 0, 0, 2, 1, 2, 2, 3, 2, 0, 3, 0, 2, 4, 2, 0, 2, 2, 2, 2, 0, 0, 3, 0, 4, 2, 0, 0, 4, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 4, 2, 2, 0, 0, 0, 0, 3, 0, 0, 0, 2, 0, 2, 0, 0, 2, 2, 4, 1, 2, 0, 2, 2, 0, 2, 0, 2, 0, 0, 3, 1, 2, 0, 4, 0, 2, 0, 0, 2, 3, 4, 2, 4, 2, 0, 2, 0, 0, 1, 0, 2, 2, 2, 0, 2, 4, 3, 0, 3, 2, 2, 2, 2, 3, 0, 2, 0, 3, 2, 4, 0, 3, 2, 2, 2, 4, 0, 2, 4, 0, 0, 0, 2, 0, 0, 4, 0, 0, 0, 2, 0, 4, 0, 4, 0, 2, 3, 3, 3, 2, 3, 2, 2, 1, 4, 2, 3, 4, 0, 0, 0, 0, 4, 0, 3, 0, 2, 3, 2, 4, 3, 2, 0, 0, 2, 2, 3, 0, 4, 2, 0, 0, 0, 2, 0, 0, 0, 3, 0, 2, 2, 0, 0, 2, 2, 0, 3, 2, 0, 0, 0, 2, 0, 0, 0, 2, 4, 0, 2, 0, 0, 0, 4, 0, 2, 4, 2, 0, 1, 0, 0, 2, 0, 2, 0, 4, 2, 4, 2, 0, 0, 2, 0, 0, 4, 0, 2, 4, 2, 0, 3, 0, 4, 0, 2, 2, 0, 0, 3, 

In [ ]:
print(probabilities_inc_shuf1)
print(probabilities_inc_shuf2)
print(probabilities_inc_shuf3)

Streaming output truncated to the last 5000 lines.
        2.7333064e-05]], dtype=float32), array([[9.9956530e-01, 2.9518630e-04, 6.2732142e-05, 4.5667864e-05,
        3.1153173e-05]], dtype=float32), array([[5.2849718e-05, 3.2016129e-04, 9.8325461e-01, 1.4599743e-02,
        1.7727062e-03]], dtype=float32), array([[9.9951780e-01, 3.6258108e-04, 6.0660419e-05, 3.4240566e-05,
        2.4763001e-05]], dtype=float32), array([[1.3466268e-05, 4.2360649e-04, 9.9856180e-01, 7.1219640e-04,
        2.8884699e-04]], dtype=float32), array([[7.5486038e-05, 1.9209173e-03, 1.2377579e-02, 3.3353343e-05,
        9.8559266e-01]], dtype=float32), array([[9.9967802e-01, 1.9092427e-04, 5.1379026e-05, 6.5489927e-05,
        1.4238746e-05]], dtype=float32), array([[9.9320579e-01, 5.7703159e-03, 8.3486288e-04, 3.9306498e-05,
        1.4974504e-04]], dtype=float32), array([[3.9972929e-05, 1.1846983e-03, 9.9697363e-01, 6.3892156e-05,
        1.7377465e-03]], dtype=float32), array([[9.9952638e-01, 3.6044591e-04

In [ ]:
print(probabilities_shuf1)
print(probabilities_shuf2)
print(probabilities_shuf3)

Streaming output truncated to the last 5000 lines.
        2.8658993e-04]], dtype=float32), array([[9.9893969e-01, 3.2339172e-04, 4.7321085e-04, 9.4169627e-05,
        1.6939642e-04]], dtype=float32), array([[1.6068602e-04, 9.9565065e-04, 8.5320187e-01, 1.4440058e-01,
        1.2412835e-03]], dtype=float32), array([[9.97947156e-01, 1.59555301e-03, 3.31521558e-04, 1.34054735e-05,
        1.12480004e-04]], dtype=float32), array([[2.9182529e-05, 2.3514153e-03, 9.9627328e-01, 5.0847570e-04,
        8.3760347e-04]], dtype=float32), array([[2.3999158e-03, 6.0397580e-02, 2.5356913e-01, 6.2655454e-05,
        6.8357074e-01]], dtype=float32), array([[9.9971205e-01, 1.7999674e-04, 6.9415240e-05, 2.7697135e-05,
        1.0903364e-05]], dtype=float32), array([[9.9420834e-01, 4.1619278e-03, 1.4337271e-03, 4.3201246e-05,
        1.5281695e-04]], dtype=float32), array([[1.21958576e-04, 2.90093082e-03, 9.94503140e-01, 7.88024699e-05,
        2.39518820e-03]], dtype=float32), array([[9.9880111e-01, 4.8

In [ ]:
#accuracy after incrementally training and predicting on x_train_sub[0:500](hold-out set) using loaded_model_shuf1_inc
from sklearn.metrics import accuracy_score
accuracy_score(y_sub_dt[0:2457], m_vote_inc)

0.8656351791530945

In [ ]:
#accuracy after incrementally training and predicting on x_train_sub[0:500](hold-out set) using loaded_model_shuf1_inc
from sklearn.metrics import accuracy_score
accuracy_score(y_sub_dt[0:2457], m_vote)

0.8631921824104235

In [ ]:
from sklearn.metrics import confusion_matrix
matrix = confusion_matrix(y_sub_dt, m_vote_inc)
matrix.diagonal()/matrix.sum(axis=1)

array([0.9572093 , 0.08053691, 0.94899536, 0.86381323, 0.75914634])

In [ ]:
#y_sub_dt
from sklearn.metrics import precision_score, recall_score
f1_cnn = f1_score(y_sub_dt, m_vote_inc, average="macro")
prec_cnn = precision_score(y_sub_dt, m_vote_inc, average="macro")
recall_cnn = recall_score(y_sub_dt, m_vote_inc, average="macro")
if VBS:
    print("Precision: {}".format(prec_cnn)) 
    print("Recall: {}".format(recall_cnn))
    print("F1 score: {}".format(f1_cnn))

    report = classification_report(y_sub_dt, m_vote_inc, digits=6)
    print(report)

Precision: 0.7628605483981545
Recall: 0.7219402298654993
F1 score: 0.7214947838103901
              precision    recall  f1-score   support

           0   0.986577  0.957209  0.971671      1075
           1   0.363636  0.080537  0.131868       149
           2   0.743341  0.948995  0.833673       647
           3   0.932773  0.863813  0.896970       257
           4   0.787975  0.759146  0.773292       328

    accuracy                       0.865635      2456
   macro avg   0.762861  0.721940  0.721495      2456
weighted avg   0.852554  0.865635  0.850058      2456



In [ ]:
x_train_with_semi_sup_labels=x_sub_set

In [ ]:
x_train_with_semi_sup_labels['pseudo_labels']=m_vote_inc

In [ ]:
x_train_with_semi_sup_labels

0         1         2         3         4         5         6  \
0    -0.037317 -0.035184 -0.053523 -0.013007  0.056081  0.106405  0.121332   
1     0.022085 -0.017796 -0.064110 -0.042669 -0.010506  0.002359 -0.012222   
2    -0.127577 -0.109566 -0.066254 -0.008791 -0.037952 -0.106564 -0.128006   
3    -0.147303 -0.149447 -0.105278 -0.070971 -0.057678 -0.042240 -0.037523   
4    -0.071861 -0.088920 -0.128156 -0.128156 -0.117920 -0.088067 -0.066743   
...        ...       ...       ...       ...       ...       ...       ...   
2451 -0.002359  0.139156 -0.008791  0.067970  0.106136  0.143015  0.113426   
2452 -0.136259 -0.109391 -0.123891 -0.130714 -0.159288 -0.149053 -0.161847   
2453  0.016081  0.049101 -0.076117 -0.019083 -0.055534 -0.042669 -0.136583   
2454 -0.009220 -0.006647 -0.006218 -0.010506  0.011364 -0.017368 -0.025515   
2455  0.007890 -0.079964 -0.121332 -0.080390 -0.072714 -0.021963  0.009596   

             7         8         9  ...      2991      2992      2993  \
0     0.129435  0.153744  0.198097  ... -0.088920 -0.118773 -0.130714   
1    -0.040524 -0.072258 -0.054247  ...  0.119858  0.074831 -0.004503   
2    -0.106993 -0.100132 -0.077833  ... -0.001501  0.037952  0.036665   
3    -0.040953 -0.046957 -0.017796  ...  0.239931  0.229639  0.205624   
4    -0.033478 -0.030919 -0.008743  ...  0.031772 -0.009596 -0.039875   
...        ...       ...       ...  ...       ...       ...       ...   
2451  0.005789  0.059822  0.031948  ... -0.274666 -0.113855 -0.155022   
2452 -0.102141 -0.091905 -0.026228  ... -0.175068 -0.268039 -0.137538   
2453 -0.041811 -0.082550 -0.010078  ... -0.121573 -0.110424 -0.085123   
2454 -0.032377 -0.011793  0.010935  ... -0.045242 -0.006218  0.029804   
2455  0.013434  0.027081 -0.027934  ...  0.027508  0.044567  0.044993   

          2994      2995      2996      2997      2998      2999  \
0    -0.128156 -0.092332 -0.072287 -0.056081 -0.107685 -0.138817   
1    -0.031090 -0.081263 -0.052103 -0.084265 -0.057249 -0.053389   
2     0.046528  0.048243  0.011364  0.021656  0.037094  0.021656   
3     0.192759  0.182039  0.137869  0.111710  0.105278  0.122860   
4    -0.053523 -0.083802 -0.053096 -0.012581 -0.015140  0.001919   
...        ...       ...       ...       ...       ...       ...   
2451  0.121145 -0.032377  0.225350 -0.048672 -0.414036 -0.345852   
2452 -0.193406 -0.041581 -0.178906 -0.052243 -0.233495 -0.170376   
2453 -0.070114 -0.073544 -0.042240 -0.027231  0.014366 -0.018225   
2454  0.075260  0.103991  0.104420  0.073544  0.057678  0.033663   
2455  0.051817  0.078685  0.100435  0.136685  0.148626  0.104273   

      pseudo_labels  
0                 2  
1                 2  
2                 4  
3                 2  
4                 2  
...             ...  
2451              0  
2452              0  
2453              1  
2454              2  
2455              2  

[2456 rows x 3001 columns]

In [ ]:
x_train_with_semi_sup_labels.to_csv(r'/content/gdrive/My Drive/physionet/ensemble/50_subs/x_train_with_inc_semi_sup_labels_train_on_batch_trial_4.csv', header=False, index=False)

In [ ]:
#classic incremental learning, not semi supervised inc

In [ ]:
checkpoint_path_model_inc_shuf1 = "/content/gdrive/My Drive/physionet/ensemble_classic_inc/model_shuf1/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_inc_shuf1 = os.path.dirname(checkpoint_path_model_inc_shuf1)
cp_callback_model_new_shuf1 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_inc_shuf1,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
checkpoint_path_model_inc_shuf2 = "/content/gdrive/My Drive/physionet/ensemble_classic_inc/model_shuf2/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_inc_shuf2 = os.path.dirname(checkpoint_path_model_inc_shuf2)
cp_callback_model_new_shuf2 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_inc_shuf2,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
checkpoint_path_model_inc_shuf3 = "/content/gdrive/My Drive/physionet/ensemble_classic_inc/model_shuf3/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_inc_shuf3 = os.path.dirname(checkpoint_path_model_inc_shuf3)
cp_callback_model_new_shuf3 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_inc_shuf3,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
preds_shuf1=[]
preds_inc_shuf1=[]
probabilities_shuf1=[]
probabilities_inc_shuf1=[]


count_shuf1=0

preds_shuf2=[]
preds_inc_shuf2=[]
probabilities_shuf2=[]
probabilities_inc_shuf2=[]

count_shuf2=0

preds_shuf3=[]
preds_inc_shuf3=[]
probabilities_shuf3=[]
probabilities_inc_shuf3=[]

cnt_shuf3=0

m_vote_inc=[]

m_vote=[]

count_status1=0
count_status2=0
count_status3=0

for sple in np.array(x_sub_set[0:1980]):

  sple_rshp=sple.reshape(1,3000,1)



  p1_i=loaded_model_shuf1.predict(sple_rshp)

  p1_i_fin=np.argmax(p1_i,axis=1)

  preds_shuf1.append(np.asscalar(p1_i_fin))

  probabilities_shuf1.append(p1_i) 

  
    
  p1_i_inc=loaded_model_shuf1_new.predict_on_batch(sple_rshp)

  p1_i_inc_fin=np.argmax(p1_i_inc,axis=1)

  

  #count_shuf1+=1

  p2_i=loaded_model_shuf2.predict(sple_rshp)

  p2_i_fin=np.argmax(p2_i,axis=1)

  preds_shuf2.append(np.asscalar(p2_i_fin))

  probabilities_shuf2.append(p2_i)

  
    
  p2_i_inc=loaded_model_shuf2_new.predict_on_batch(sple_rshp)

  p2_i_inc_fin=np.argmax(p2_i_inc,axis=1)

  

  #count_shuf2+=1

  p3_i=loaded_model_shuf3.predict(sple_rshp)

  p3_i_fin=np.argmax(p3_i,axis=1)

  preds_shuf3.append(np.asscalar(p3_i_fin))

  probabilities_shuf3.append(p3_i)

  
    
  p3_i_inc=loaded_model_shuf3_new.predict_on_batch(sple_rshp)

  p3_i_inc_fin=np.argmax(p3_i_inc,axis=1)

  



  preds_inc_shuf1.append(np.asscalar(p1_i_inc_fin))

  probabilities_inc_shuf1.append(p1_i_inc)


  preds_inc_shuf2.append(np.asscalar(p2_i_inc_fin))

  probabilities_inc_shuf2.append(p2_i_inc)


  preds_inc_shuf3.append(np.asscalar(p3_i_inc_fin))

  probabilities_inc_shuf3.append(p3_i_inc)



  mode_i_inc=mode([np.asscalar(p1_i_inc_fin),np.asscalar(p2_i_inc_fin),np.asscalar(p3_i_inc_fin)])
  m_vote_i_inc=mode_i_inc[0][0]
  m_vote_inc.append(m_vote_i_inc)

  mode_i=mode([np.asscalar(p1_i_fin),np.asscalar(p2_i_fin),np.asscalar(p3_i_fin)])
  m_vote_i=mode_i[0][0]
  m_vote.append(m_vote_i)


  p1_i_inc_fin_=np_utils.to_categorical(np.asscalar(p1_i_inc_fin), num_classes=5)
  p2_i_inc_fin_=np_utils.to_categorical(np.asscalar(p2_i_inc_fin), num_classes=5)
  p3_i_inc_fin_=np_utils.to_categorical(np.asscalar(p3_i_inc_fin), num_classes=5)

  p1_i_inc_fin_.shape=(1,5)
  p2_i_inc_fin_.shape=(1,5)
  p3_i_inc_fin_.shape=(1,5)

   

  

  loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

  

  loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

  

  loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)




In [ ]:
print(m_vote)
print(m_vote_inc)

[4, 2, 0, 4, 2, 4, 0, 2, 2, 1, 0, 2, 4, 2, 2, 4, 0, 0, 0, 0, 0, 4, 4, 2, 2, 0, 0, 2, 4, 4, 4, 0, 2, 2, 4, 2, 0, 4, 0, 2, 4, 4, 4, 0, 1, 0, 0, 0, 2, 4, 0, 2, 2, 1, 1, 2, 3, 2, 3, 2, 0, 2, 2, 2, 0, 1, 0, 1, 2, 0, 4, 0, 2, 3, 2, 0, 0, 3, 0, 1, 2, 0, 2, 2, 2, 1, 4, 2, 2, 0, 1, 4, 0, 2, 3, 0, 3, 2, 2, 2, 4, 2, 2, 2, 4, 2, 2, 1, 3, 0, 0, 2, 2, 0, 0, 4, 2, 2, 0, 4, 2, 2, 2, 2, 2, 3, 3, 2, 2, 0, 0, 0, 4, 2, 2, 4, 2, 2, 2, 4, 2, 4, 0, 2, 0, 0, 2, 4, 2, 4, 2, 0, 4, 0, 1, 4, 0, 2, 0, 2, 0, 3, 3, 0, 1, 2, 1, 0, 1, 2, 2, 0, 2, 0, 2, 1, 1, 0, 3, 2, 1, 2, 4, 2, 0, 4, 3, 2, 2, 2, 2, 2, 0, 2, 0, 0, 4, 2, 0, 2, 4, 1, 3, 0, 2, 2, 4, 1, 0, 2, 4, 0, 2, 2, 2, 2, 0, 2, 4, 4, 4, 2, 0, 0, 2, 2, 0, 2, 3, 1, 2, 2, 2, 0, 1, 2, 0, 3, 4, 2, 2, 2, 2, 3, 1, 0, 2, 0, 2, 3, 2, 4, 0, 2, 0, 2, 2, 0, 2, 2, 1, 1, 2, 4, 1, 4, 0, 2, 2, 0, 4, 4, 0, 0, 2, 2, 2, 2, 4, 2, 0, 2, 0, 0, 4, 0, 0, 2, 4, 2, 0, 2, 0, 3, 2, 2, 2, 0, 2, 3, 4, 2, 2, 0, 0, 0, 2, 0, 2, 2, 2, 2, 1, 2, 4, 3, 0, 1, 2, 0, 0, 3, 0, 0, 2, 2, 0, 2, 0, 2, 2, 1, 2, 

In [ ]:
print(probabilities_inc_shuf1)
print(probabilities_inc_shuf2)
print(probabilities_inc_shuf3)

Streaming output truncated to the last 5000 lines.
        7.626257e-04]], dtype=float32), array([[1.0938323e-05, 2.7213022e-04, 9.9894935e-01, 2.5329334e-04,
        5.1433168e-04]], dtype=float32), array([[2.1420197e-04, 1.9266957e-03, 5.8377732e-02, 5.3873973e-05,
        9.3942744e-01]], dtype=float32), array([[5.2753210e-05, 6.6705450e-04, 9.9590850e-01, 1.6487384e-03,
        1.7229841e-03]], dtype=float32), array([[1.5196139e-05, 6.2004768e-04, 9.9860090e-01, 1.2801944e-04,
        6.3596538e-04]], dtype=float32), array([[9.9739766e-01, 4.4504803e-04, 1.4392072e-03, 2.2302252e-04,
        4.9512612e-04]], dtype=float32), array([[6.3583924e-05, 1.5449061e-04, 2.0574766e-01, 7.9384547e-01,
        1.8878412e-04]], dtype=float32), array([[9.0019195e-05, 8.1620907e-04, 2.8084896e-03, 3.4507146e-05,
        9.9625081e-01]], dtype=float32), array([[2.6132002e-05, 2.5154196e-04, 9.9774253e-01, 1.2614685e-03,
        7.1829098e-04]], dtype=float32), array([[4.3663273e-05, 9.4741862e-04,

In [ ]:
print(probabilities_shuf1)
print(probabilities_shuf2)
print(probabilities_shuf3)

Streaming output truncated to the last 5000 lines.
        3.9083855e-03]], dtype=float32), array([[3.4275916e-05, 1.3155226e-03, 9.9645412e-01, 9.8988262e-04,
        1.2062397e-03]], dtype=float32), array([[1.7969931e-02, 2.1967623e-01, 1.6978370e-01, 4.7463102e-05,
        5.9252268e-01]], dtype=float32), array([[0.00809282, 0.17200108, 0.8058373 , 0.00810249, 0.00596643]],
      dtype=float32), array([[6.8431924e-05, 6.0367906e-03, 9.9127418e-01, 3.7678040e-04,
        2.2438932e-03]], dtype=float32), array([[9.9843127e-01, 1.3125482e-03, 1.5533163e-04, 2.6424448e-05,
        7.4422889e-05]], dtype=float32), array([[4.2916348e-05, 6.8249654e-05, 1.5182900e-02, 9.8468459e-01,
        2.1355436e-05]], dtype=float32), array([[9.3987735e-04, 3.4098912e-02, 3.9538309e-02, 5.1687512e-05,
        9.2537129e-01]], dtype=float32), array([[3.4875923e-04, 2.0197954e-03, 7.5464779e-01, 2.4202077e-01,
        9.6283946e-04]], dtype=float32), array([[1.9554312e-03, 1.1199443e-01, 1.3168761e-01, 

In [ ]:
#accuracy after incrementally training and predicting on x_train_sub[0:500](hold-out set) using loaded_model_shuf1_inc
from sklearn.metrics import accuracy_score
accuracy_score(y_sub_dt[0:1980], m_vote_inc)

0.7101010101010101

In [ ]:
#accuracy after incrementally training and predicting on x_train_sub[0:500](hold-out set) using loaded_model_shuf1_inc
from sklearn.metrics import accuracy_score
accuracy_score(y_sub_dt[0:1980], m_vote)

0.8373737373737373

In [ ]:
from sklearn.metrics import confusion_matrix
matrix = confusion_matrix(y_sub_dt, m_vote_inc)
matrix.diagonal()/matrix.sum(axis=1)

array([0.64923077, 0.00571429, 0.984375  , 0.26553672, 0.88686131])

In [ ]:
from sklearn.metrics import precision_score, recall_score
f1_cnn = f1_score(y_sub_dt, m_vote_inc, average="macro")
prec_cnn = precision_score(y_sub_dt, m_vote_inc, average="macro")
recall_cnn = recall_score(y_sub_dt, m_vote_inc, average="macro")
if VBS:
    print("Precision: {}".format(prec_cnn)) 
    print("Recall: {}".format(recall_cnn))
    print("F1 score: {}".format(f1_cnn))

    report = classification_report(y_sub_dt, m_vote_inc, digits=6)
    print(report)

Precision: 0.6628469041789604
Recall: 0.558343618395502
F1 score: 0.5346788993780548
              precision    recall  f1-score   support

           0   0.956916  0.649231  0.773602       650
           1   0.200000  0.005714  0.011111       175
           2   0.662524  0.984375  0.792000       704
           3   0.940000  0.265537  0.414097       177
           4   0.554795  0.886861  0.682584       274

    accuracy                       0.710101      1980
   macro avg   0.662847  0.558344  0.534679      1980
weighted avg   0.728185  0.710101  0.668019      1980



In [ ]:
x_train_classic_labels=x_sub_set

In [ ]:
x_train_classic_labels['pseudo_labels']=m_vote_inc

In [ ]:
x_train_classic_labels.to_csv(r'/content/gdrive/My Drive/physionet/ensemble/50_subs/x_train_with_classic_labels_trial_10.csv', header=False, index=False)

## simple incremental tri-training 

In [ ]:
checkpoint_path_model_shuf1 = "/content/gdrive/My Drive/physionet/ensemble_simple_inc_tri_train/model_shuf1/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_shuf1 = os.path.dirname(checkpoint_path_model_shuf1)
cp_callback_model_shuf1 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_shuf1,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
checkpoint_path_model_shuf2 = "/content/gdrive/My Drive/physionet/ensemble_simple_inc_tri_train/model_shuf2/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_shuf2 = os.path.dirname(checkpoint_path_model_shuf2)
cp_callback_model_shuf2 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_shuf2,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
checkpoint_path_model_shuf3 = "/content/gdrive/My Drive/physionet/ensemble_simple_inc_tri_train/model_shuf3/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_shuf3 = os.path.dirname(checkpoint_path_model_shuf3)
cp_callback_model_shuf3 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_shuf3,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
preds_shuf1=[]
preds_inc_shuf1=[]
probabilities_shuf1=[]
probabilities_inc_shuf1=[]


count_shuf1=0

preds_shuf2=[]
preds_inc_shuf2=[]
probabilities_shuf2=[]
probabilities_inc_shuf2=[]

count_shuf2=0

preds_shuf3=[]
preds_inc_shuf3=[]
probabilities_shuf3=[]
probabilities_inc_shuf3=[]

cnt_shuf3=0

m_vote_inc=[]

m_vote=[]

count_status1=0
count_status2=0
count_status3=0

for sple in np.array(x_sub_set[0:1980]):

  sple_rshp=sple.reshape(1,3000,1)



  p1_i=loaded_model_shuf1.predict(sple_rshp)

  p1_i_fin=np.argmax(p1_i,axis=1)

  preds_shuf1.append(np.asscalar(p1_i_fin))

  probabilities_shuf1.append(p1_i) 

  
  
  p1_i_inc=loaded_model_shuf1_new.predict_on_batch(sple_rshp)

  p1_i_inc_fin=np.argmax(p1_i_inc,axis=1)

  
  #count_shuf1+=1

  p2_i=loaded_model_shuf2.predict(sple_rshp)

  p2_i_fin=np.argmax(p2_i,axis=1)

  preds_shuf2.append(np.asscalar(p2_i_fin))

  probabilities_shuf2.append(p2_i)

  
    
  p2_i_inc=loaded_model_shuf2_new.predict_on_batch(sple_rshp)

  p2_i_inc_fin=np.argmax(p2_i_inc,axis=1)

  
  #count_shuf2+=1

  p3_i=loaded_model_shuf3.predict(sple_rshp)

  p3_i_fin=np.argmax(p3_i,axis=1)

  preds_shuf3.append(np.asscalar(p3_i_fin))

  probabilities_shuf3.append(p3_i)

  count_status3+=1

  
  p3_i_inc=loaded_model_shuf3_new.predict_on_batch(sple_rshp)

  p3_i_inc_fin=np.argmax(p3_i_inc,axis=1)

  

  preds_inc_shuf1.append(np.asscalar(p1_i_inc_fin))

  probabilities_inc_shuf1.append(p1_i_inc)


  preds_inc_shuf2.append(np.asscalar(p2_i_inc_fin))

  probabilities_inc_shuf2.append(p2_i_inc)


  preds_inc_shuf3.append(np.asscalar(p3_i_inc_fin))

  probabilities_inc_shuf3.append(p3_i_inc)




  mode_i_inc=mode([np.asscalar(p1_i_inc_fin),np.asscalar(p2_i_inc_fin),np.asscalar(p3_i_inc_fin)])
  m_vote_i_inc=mode_i_inc[0][0]
  m_vote_inc.append(m_vote_i_inc)

  mode_i=mode([np.asscalar(p1_i_fin),np.asscalar(p2_i_fin),np.asscalar(p3_i_fin)])
  m_vote_i=mode_i[0][0]
  m_vote.append(m_vote_i)

  #count_shuf3+=1

  #if (p1_i_inc_fin != p1_i_fin):
   # p1_i_inc_fin=p1_i_fin

  #if (p2_i_inc_fin != p2_i_fin):
   # p2_i_inc_fin=p2_i_fin

  #if (p3_i_inc_fin != p3_i_fin):
   # p3_i_inc_fin=p3_i_fin

  
  #p1_i_inc_fin_vals=np.asscalar(p1_i_inc_fin)
  #p2_i_inc_fin_vals=np.asscalar(p2_i_inc_fin)
  #p3_i_inc_fin_vals=np.asscalar(p3_i_inc_fin)

  

  p1_i_inc_fin_=np_utils.to_categorical(np.asscalar(p1_i_inc_fin), num_classes=5)
  p2_i_inc_fin_=np_utils.to_categorical(np.asscalar(p2_i_inc_fin), num_classes=5)
  p3_i_inc_fin_=np_utils.to_categorical(np.asscalar(p3_i_inc_fin), num_classes=5)

  p1_i_inc_fin_.shape=(1,5)
  p2_i_inc_fin_.shape=(1,5)
  p3_i_inc_fin_.shape=(1,5)

  

  if (p2_i_inc_fin==p3_i_inc_fin):
    
    p1_i_inc_fin=p3_i_inc_fin

    p1_i_inc_fin_=np_utils.to_categorical(np.asscalar(p1_i_inc_fin), num_classes=5)

    p1_i_inc_fin_.shape=(1,5)

    #p1_i_inc_fin=np.argmax(p1_i_inc,axis=1)

    
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

    

        
   
        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

   


   
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)

    
     

  elif (p3_i_inc_fin==p1_i_inc_fin):
    
    p2_i_inc_fin=p1_i_inc_fin

    p2_i_inc_fin_=np_utils.to_categorical(np.asscalar(p2_i_inc_fin), num_classes=5)

    p2_i_inc_fin_.shape=(1,5)

    #p2_i_inc_fin=np.argmax(p2_i_inc,axis=1)

    
        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

    
   
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

    

    
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)

    
  elif (p2_i_inc_fin==p1_i_inc_fin):
    
    p3_i_inc_fin=p1_i_inc_fin

    p3_i_inc_fin_=np_utils.to_categorical(np.asscalar(p3_i_inc_fin), num_classes=5)

    p3_i_inc_fin_.shape=(1,5)

    #p3_i_inc_fin=np.argmax(p3_i_inc,axis=1)

    
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)
   


    
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

       
    

    
        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

   
  
 

  else:
 
      
   
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

    
    
        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

    

    
    
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)

     
  

In [ ]:
print(m_vote)
print(m_vote_inc)

[4, 2, 0, 4, 2, 4, 0, 2, 2, 1, 0, 2, 4, 2, 2, 4, 0, 0, 0, 0, 0, 4, 4, 2, 2, 0, 0, 2, 4, 4, 4, 0, 2, 2, 4, 2, 0, 4, 0, 2, 4, 4, 4, 0, 1, 0, 0, 0, 2, 4, 0, 2, 2, 1, 1, 2, 3, 2, 3, 2, 0, 2, 2, 2, 0, 1, 0, 1, 2, 0, 4, 0, 2, 3, 2, 0, 0, 3, 0, 1, 2, 0, 2, 2, 2, 1, 4, 2, 2, 0, 1, 4, 0, 2, 3, 0, 3, 2, 2, 2, 4, 2, 2, 2, 4, 2, 2, 1, 3, 0, 0, 2, 2, 0, 0, 4, 2, 2, 0, 4, 2, 2, 2, 2, 2, 3, 3, 2, 2, 0, 0, 0, 4, 2, 2, 4, 2, 2, 2, 4, 2, 4, 0, 2, 0, 0, 2, 4, 2, 4, 2, 0, 4, 0, 1, 4, 0, 2, 0, 2, 0, 3, 3, 0, 1, 2, 1, 0, 1, 2, 2, 0, 2, 0, 2, 1, 1, 0, 3, 2, 1, 2, 4, 2, 0, 4, 3, 2, 2, 2, 2, 2, 0, 2, 0, 0, 4, 2, 0, 2, 4, 1, 3, 0, 2, 2, 4, 1, 0, 2, 4, 0, 2, 2, 2, 2, 0, 2, 4, 4, 4, 2, 0, 0, 2, 2, 0, 2, 3, 1, 2, 2, 2, 0, 1, 2, 0, 3, 4, 2, 2, 2, 2, 3, 1, 0, 2, 0, 2, 3, 2, 4, 0, 2, 0, 2, 2, 0, 2, 2, 1, 1, 2, 4, 1, 4, 0, 2, 2, 0, 4, 4, 0, 0, 2, 2, 2, 2, 4, 2, 0, 2, 0, 0, 4, 0, 0, 2, 4, 2, 0, 2, 0, 3, 2, 2, 2, 0, 2, 3, 4, 2, 2, 0, 0, 0, 2, 0, 2, 2, 2, 2, 1, 2, 4, 3, 0, 1, 2, 0, 0, 3, 0, 0, 2, 2, 0, 2, 0, 2, 2, 1, 2, 

In [ ]:
print(probabilities_inc_shuf1)
print(probabilities_inc_shuf2)
print(probabilities_inc_shuf3)

Streaming output truncated to the last 5000 lines.
        6.2738877e-04]], dtype=float32), array([[1.8476441e-05, 2.6523066e-04, 9.9908423e-01, 1.0937668e-04,
        5.2276999e-04]], dtype=float32), array([[1.9785226e-04, 1.8343369e-03, 3.0597258e-02, 3.1820808e-05,
        9.6733874e-01]], dtype=float32), array([[3.8759496e-05, 4.5603394e-04, 9.9806660e-01, 8.0260017e-04,
        6.3590094e-04]], dtype=float32), array([[2.1931710e-05, 6.6894444e-04, 9.9855345e-01, 7.3672112e-05,
        6.8201032e-04]], dtype=float32), array([[9.9941146e-01, 2.3516997e-04, 1.8060363e-04, 6.4373191e-05,
        1.0843149e-04]], dtype=float32), array([[4.3800421e-05, 3.3534126e-04, 9.9259418e-01, 6.5423427e-03,
        4.8430520e-04]], dtype=float32), array([[7.2973286e-05, 8.9055666e-04, 3.1212475e-03, 3.4035100e-05,
        9.9588120e-01]], dtype=float32), array([[2.6967944e-05, 2.7082313e-04, 9.9854952e-01, 2.9083248e-04,
        8.6177926e-04]], dtype=float32), array([[4.1605810e-05, 1.2622355e-03

In [ ]:
print(probabilities_shuf1)
print(probabilities_shuf2)
print(probabilities_shuf3)

Streaming output truncated to the last 5000 lines.
        3.9083892e-03]], dtype=float32), array([[3.4275916e-05, 1.3155232e-03, 9.9645412e-01, 9.8988262e-04,
        1.2062407e-03]], dtype=float32), array([[1.7969940e-02, 2.1967630e-01, 1.6978367e-01, 4.7463094e-05,
        5.9252262e-01]], dtype=float32), array([[0.00809282, 0.17200108, 0.8058373 , 0.00810248, 0.00596643]],
      dtype=float32), array([[6.8431924e-05, 6.0367938e-03, 9.9127418e-01, 3.7678002e-04,
        2.2438942e-03]], dtype=float32), array([[9.9843127e-01, 1.3125482e-03, 1.5533163e-04, 2.6424448e-05,
        7.4422889e-05]], dtype=float32), array([[4.2916348e-05, 6.8249654e-05, 1.5182916e-02, 9.8468459e-01,
        2.1355452e-05]], dtype=float32), array([[9.3987683e-04, 3.4098916e-02, 3.9538320e-02, 5.1687555e-05,
        9.2537117e-01]], dtype=float32), array([[3.4875909e-04, 2.0197954e-03, 7.5464779e-01, 2.4202077e-01,
        9.6283946e-04]], dtype=float32), array([[1.9554328e-03, 1.1199445e-01, 1.3168767e-01, 

In [ ]:
#accuracy after incrementally training and predicting on x_train_sub[0:500](hold-out set) using loaded_model_shuf1_inc
from sklearn.metrics import accuracy_score
accuracy_score(y_sub_dt[0:1980], m_vote_inc)

0.7333333333333333

In [ ]:
#accuracy after incrementally training and predicting on x_train_sub[0:500](hold-out set) using loaded_model_shuf1_inc
from sklearn.metrics import accuracy_score
accuracy_score(y_sub_dt[0:1980], m_vote)

0.8373737373737373

In [ ]:
from sklearn.metrics import confusion_matrix
matrix = confusion_matrix(y_sub_dt, m_vote_inc)
matrix.diagonal()/matrix.sum(axis=1)

array([0.76      , 0.01714286, 0.99147727, 0.07344633, 0.89051095])

In [ ]:
from sklearn.metrics import precision_score, recall_score
f1_cnn = f1_score(y_sub_dt, m_vote_inc, average="macro")
prec_cnn = precision_score(y_sub_dt, m_vote_inc, average="macro")
recall_cnn = recall_score(y_sub_dt, m_vote_inc, average="macro")
if VBS:
    print("Precision: {}".format(prec_cnn)) 
    print("Recall: {}".format(recall_cnn))
    print("F1 score: {}".format(f1_cnn))

    report = classification_report(y_sub_dt, m_vote_inc, digits=6)
    print(report)

Precision: 0.7176312854354494
Recall: 0.546515481291771
F1 score: 0.5050627788545985
              precision    recall  f1-score   support

           0   0.950000  0.760000  0.844444       650
           1   0.375000  0.017143  0.032787       175
           2   0.687685  0.991477  0.812100       704
           3   1.000000  0.073446  0.136842       177
           4   0.575472  0.890511  0.699140       274

    accuracy                       0.733333      1980
   macro avg   0.717631  0.546515  0.505063      1980
weighted avg   0.758553  0.733333  0.677844      1980



In [ ]:
x_train_with_simple_tri_trained_labels=x_sub_set

In [ ]:
x_train_with_simple_tri_trained_labels['pseudo_labels']=m_vote_inc

In [ ]:
x_train_with_simple_tri_trained_labels.to_csv(r'/content/gdrive/My Drive/physionet/ensemble/50_subs/x_train_with_simple_tri_trained_labels_frozen_layers_train_on_batch_trial_10.csv', header=False, index=False)

##Incremental semi supervised Learning with Tri-Training, majority voting (final modified code)

In [ ]:
checkpoint_path_model_shuf1 = "/content/gdrive/My Drive/physionet/ensemble_inc_semi_sup_tri_train/model_shuf1/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_shuf1 = os.path.dirname(checkpoint_path_model_shuf1)
cp_callback_model_shuf1 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_shuf1,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
checkpoint_path_model_shuf2 = "/content/gdrive/My Drive/physionet/ensemble_inc_semi_sup_tri_train/model_shuf2/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_shuf2 = os.path.dirname(checkpoint_path_model_shuf2)
cp_callback_model_shuf2 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_shuf2,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
checkpoint_path_model_shuf3 = "/content/gdrive/My Drive/physionet/ensemble_inc_semi_sup_tri_train/model_shuf3/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_shuf3 = os.path.dirname(checkpoint_path_model_shuf3)
cp_callback_model_shuf3 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_shuf3,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
preds_shuf1=[]
preds_inc_shuf1=[]
probabilities_shuf1=[]
probabilities_inc_shuf1=[]


count_shuf1=0

preds_shuf2=[]
preds_inc_shuf2=[]
probabilities_shuf2=[]
probabilities_inc_shuf2=[]

count_shuf2=0

preds_shuf3=[]
preds_inc_shuf3=[]
probabilities_shuf3=[]
probabilities_inc_shuf3=[]

cnt_shuf3=0

m_vote_inc=[]

m_vote=[]

count_status1=0
count_status2=0
count_status3=0

for sple in np.array(x_sub_set[0:1980]):

  sple_rshp=sple.reshape(1,3000,1)



  p1_i=loaded_model_shuf1.predict(sple_rshp)

  p1_i_fin=np.argmax(p1_i,axis=1)

  preds_shuf1.append(np.asscalar(p1_i_fin))

  probabilities_shuf1.append(p1_i) 

  
  
  p1_i_inc=loaded_model_shuf1_new.predict_on_batch(sple_rshp)

  p1_i_inc_fin=np.argmax(p1_i_inc,axis=1)

  
  #count_shuf1+=1

  p2_i=loaded_model_shuf2.predict(sple_rshp)

  p2_i_fin=np.argmax(p2_i,axis=1)

  preds_shuf2.append(np.asscalar(p2_i_fin))

  probabilities_shuf2.append(p2_i)

  
    
  p2_i_inc=loaded_model_shuf2_new.predict_on_batch(sple_rshp)

  p2_i_inc_fin=np.argmax(p2_i_inc,axis=1)

  
  #count_shuf2+=1

  p3_i=loaded_model_shuf3.predict(sple_rshp)

  p3_i_fin=np.argmax(p3_i,axis=1)

  preds_shuf3.append(np.asscalar(p3_i_fin))

  probabilities_shuf3.append(p3_i)

  count_status3+=1

  
  p3_i_inc=loaded_model_shuf3_new.predict_on_batch(sple_rshp)

  p3_i_inc_fin=np.argmax(p3_i_inc,axis=1)

  

  preds_inc_shuf1.append(np.asscalar(p1_i_inc_fin))

  probabilities_inc_shuf1.append(p1_i_inc)


  preds_inc_shuf2.append(np.asscalar(p2_i_inc_fin))

  probabilities_inc_shuf2.append(p2_i_inc)


  preds_inc_shuf3.append(np.asscalar(p3_i_inc_fin))

  probabilities_inc_shuf3.append(p3_i_inc)




  mode_i_inc=mode([np.asscalar(p1_i_inc_fin),np.asscalar(p2_i_inc_fin),np.asscalar(p3_i_inc_fin)])
  m_vote_i_inc=mode_i_inc[0][0]
  m_vote_inc.append(m_vote_i_inc)

  mode_i=mode([np.asscalar(p1_i_fin),np.asscalar(p2_i_fin),np.asscalar(p3_i_fin)])
  m_vote_i=mode_i[0][0]
  m_vote.append(m_vote_i)

  #count_shuf3+=1

  if (p1_i_inc_fin != p1_i_fin):
    p1_i_inc_fin=p1_i_fin

  if (p2_i_inc_fin != p2_i_fin):
    p2_i_inc_fin=p2_i_fin

  if (p3_i_inc_fin != p3_i_fin):
    p3_i_inc_fin=p3_i_fin

  
  #p1_i_inc_fin_vals=np.asscalar(p1_i_inc_fin)
  #p2_i_inc_fin_vals=np.asscalar(p2_i_inc_fin)
  #p3_i_inc_fin_vals=np.asscalar(p3_i_inc_fin)

  

  p1_i_inc_fin_=np_utils.to_categorical(np.asscalar(p1_i_inc_fin), num_classes=5)
  p2_i_inc_fin_=np_utils.to_categorical(np.asscalar(p2_i_inc_fin), num_classes=5)
  p3_i_inc_fin_=np_utils.to_categorical(np.asscalar(p3_i_inc_fin), num_classes=5)

  p1_i_inc_fin_.shape=(1,5)
  p2_i_inc_fin_.shape=(1,5)
  p3_i_inc_fin_.shape=(1,5)

  

  if (p2_i_inc_fin==p3_i_inc_fin):
    
    p1_i_inc_fin=p3_i_inc_fin

    p1_i_inc_fin_=np_utils.to_categorical(np.asscalar(p1_i_inc_fin), num_classes=5)

    p1_i_inc_fin_.shape=(1,5)

    #p1_i_inc_fin=np.argmax(p1_i_inc,axis=1)

    
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

    

        
   
        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

   


   
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)

    
     

  elif (p3_i_inc_fin==p1_i_inc_fin):
    
    p2_i_inc_fin=p1_i_inc_fin

    p2_i_inc_fin_=np_utils.to_categorical(np.asscalar(p2_i_inc_fin), num_classes=5)

    p2_i_inc_fin_.shape=(1,5)

    #p2_i_inc_fin=np.argmax(p2_i_inc,axis=1)

    
        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

    
   
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

    

    
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)

    
  elif (p2_i_inc_fin==p1_i_inc_fin):
    
    p3_i_inc_fin=p1_i_inc_fin

    p3_i_inc_fin_=np_utils.to_categorical(np.asscalar(p3_i_inc_fin), num_classes=5)

    p3_i_inc_fin_.shape=(1,5)

    #p3_i_inc_fin=np.argmax(p3_i_inc,axis=1)

    
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)
   


    
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

       
    

    
        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

   
  
 

  else:
 
      
   
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

    
    
        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

    

    
    
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)

     
  

In [ ]:
print(m_vote)
print(m_vote_inc)

[4, 2, 0, 4, 2, 4, 0, 2, 2, 1, 0, 2, 4, 2, 2, 4, 0, 0, 0, 0, 0, 4, 4, 2, 2, 0, 0, 2, 4, 4, 4, 0, 2, 2, 4, 2, 0, 4, 0, 2, 4, 4, 4, 0, 1, 0, 0, 0, 2, 4, 0, 2, 2, 1, 1, 2, 3, 2, 3, 2, 0, 2, 2, 2, 0, 1, 0, 1, 2, 0, 4, 0, 2, 3, 2, 0, 0, 3, 0, 1, 2, 0, 2, 2, 2, 1, 4, 2, 2, 0, 1, 4, 0, 2, 3, 0, 3, 2, 2, 2, 4, 2, 2, 2, 4, 2, 2, 1, 3, 0, 0, 2, 2, 0, 0, 4, 2, 2, 0, 4, 2, 2, 2, 2, 2, 3, 3, 2, 2, 0, 0, 0, 4, 2, 2, 4, 2, 2, 2, 4, 2, 4, 0, 2, 0, 0, 2, 4, 2, 4, 2, 0, 4, 0, 1, 4, 0, 2, 0, 2, 0, 3, 3, 0, 1, 2, 1, 0, 1, 2, 2, 0, 2, 0, 2, 1, 1, 0, 3, 2, 1, 2, 4, 2, 0, 4, 3, 2, 2, 2, 2, 2, 0, 2, 0, 0, 4, 2, 0, 2, 4, 1, 3, 0, 2, 2, 4, 1, 0, 2, 4, 0, 2, 2, 2, 2, 0, 2, 4, 4, 4, 2, 0, 0, 2, 2, 0, 2, 3, 1, 2, 2, 2, 0, 1, 2, 0, 3, 4, 2, 2, 2, 2, 3, 1, 0, 2, 0, 2, 3, 2, 4, 0, 2, 0, 2, 2, 0, 2, 2, 1, 1, 2, 4, 1, 4, 0, 2, 2, 0, 4, 4, 0, 0, 2, 2, 2, 2, 4, 2, 0, 2, 0, 0, 4, 0, 0, 2, 4, 2, 0, 2, 0, 3, 2, 2, 2, 0, 2, 3, 4, 2, 2, 0, 0, 0, 2, 0, 2, 2, 2, 2, 1, 2, 4, 3, 0, 1, 2, 0, 0, 3, 0, 0, 2, 2, 0, 2, 0, 2, 2, 1, 2, 

In [ ]:
print(probabilities_inc_shuf1)
print(probabilities_inc_shuf2)
print(probabilities_inc_shuf3)

Streaming output truncated to the last 5000 lines.
        4.9425854e-04]], dtype=float32), array([[1.1619144e-05, 1.3102735e-03, 9.9783701e-01, 2.8082769e-04,
        5.6025706e-04]], dtype=float32), array([[3.5557062e-03, 3.3379108e-01, 1.0234636e-01, 4.6078672e-05,
        5.6026083e-01]], dtype=float32), array([[2.3808278e-04, 1.2451819e-02, 9.7875369e-01, 7.3208530e-03,
        1.2356585e-03]], dtype=float32), array([[1.8005750e-05, 3.9947294e-03, 9.9509358e-01, 2.6193651e-04,
        6.3177536e-04]], dtype=float32), array([[9.9879211e-01, 1.0537055e-03, 7.7705918e-05, 5.1672156e-05,
        2.4719833e-05]], dtype=float32), array([[2.2515733e-05, 2.0732381e-05, 2.1892488e-03, 9.9776101e-01,
        6.3882731e-06]], dtype=float32), array([[1.21974015e-04, 7.23257195e-03, 8.32884852e-03, 4.07285770e-05,
        9.84275818e-01]], dtype=float32), array([[8.9803325e-05, 1.6835307e-03, 9.4930041e-01, 4.8567541e-02,
        3.5878550e-04]], dtype=float32), array([[2.2597931e-04, 4.460646

In [ ]:
print(probabilities_shuf1)
print(probabilities_shuf2)
print(probabilities_shuf3)

Streaming output truncated to the last 5000 lines.
        3.9083892e-03]], dtype=float32), array([[3.4275916e-05, 1.3155232e-03, 9.9645412e-01, 9.8988262e-04,
        1.2062407e-03]], dtype=float32), array([[1.7969940e-02, 2.1967630e-01, 1.6978367e-01, 4.7463094e-05,
        5.9252262e-01]], dtype=float32), array([[0.00809282, 0.17200108, 0.8058373 , 0.00810248, 0.00596643]],
      dtype=float32), array([[6.8431924e-05, 6.0367938e-03, 9.9127418e-01, 3.7678002e-04,
        2.2438942e-03]], dtype=float32), array([[9.9843127e-01, 1.3125482e-03, 1.5533163e-04, 2.6424448e-05,
        7.4422889e-05]], dtype=float32), array([[4.2916348e-05, 6.8249654e-05, 1.5182916e-02, 9.8468459e-01,
        2.1355452e-05]], dtype=float32), array([[9.3987683e-04, 3.4098916e-02, 3.9538320e-02, 5.1687555e-05,
        9.2537117e-01]], dtype=float32), array([[3.4875909e-04, 2.0197954e-03, 7.5464779e-01, 2.4202077e-01,
        9.6283946e-04]], dtype=float32), array([[1.9554328e-03, 1.1199445e-01, 1.3168767e-01, 

In [ ]:
#accuracy after incrementally training and predicting on x_train_sub[0:500](hold-out set) using loaded_model_shuf1_inc
from sklearn.metrics import accuracy_score
accuracy_score(y_sub_dt[0:1980], m_vote_inc)

0.8363636363636363

In [ ]:
#accuracy after incrementally training and predicting on x_train_sub[0:500](hold-out set) using loaded_model_shuf1_inc
from sklearn.metrics import accuracy_score
accuracy_score(y_sub_dt[0:1980], m_vote)

0.8373737373737373

In [ ]:
from sklearn.metrics import confusion_matrix
matrix = confusion_matrix(y_sub_dt, m_vote_inc)
matrix.diagonal()/matrix.sum(axis=1)

array([0.88615385, 0.21142857, 0.95170455, 0.82485876, 0.82846715])

In [ ]:
#y_sub_dt
from sklearn.metrics import precision_score, recall_score
f1_cnn = f1_score(y_sub_dt, m_vote_inc, average="macro")
prec_cnn = precision_score(y_sub_dt, m_vote_inc, average="macro")
recall_cnn = recall_score(y_sub_dt, m_vote_inc, average="macro")
if VBS:
    print("Precision: {}".format(prec_cnn)) 
    print("Recall: {}".format(recall_cnn))
    print("F1 score: {}".format(f1_cnn))

    report = classification_report(y_sub_dt, m_vote_inc, digits=6)
    print(report)

Precision: 0.7616807458447804
Recall: 0.7405225746767562
F1 score: 0.7485662432862474
              precision    recall  f1-score   support

           0   0.938111  0.886154  0.911392       650
           1   0.286822  0.211429  0.243421       175
           2   0.824108  0.951705  0.883322       704
           3   0.879518  0.824859  0.851312       177
           4   0.879845  0.828467  0.853383       274

    accuracy                       0.836364      1980
   macro avg   0.761681  0.740523  0.748566      1980
weighted avg   0.826712  0.836364  0.828976      1980



In [ ]:
x_sub_set

0         1         2         3         4         5         6     \
0     0.008521 -0.021337 -0.023599 -0.011384 -0.005051  0.006259  0.029784   
1     0.036570  0.025712  0.022093  0.026617  0.027974 -0.013194 -0.069290   
2     0.029801  0.029351  0.076605 -0.003951  0.022151  0.047353  0.165262   
3     0.047427  0.085428  0.082714  0.083166  0.094476  0.084523  0.072309   
4     0.416383  0.437534  0.459136  0.460486  0.450135  0.424033  0.438884   
...        ...       ...       ...       ...       ...       ...       ...   
1975  0.003997  0.004450  0.019831  0.028427  0.027974  0.005354 -0.015456   
1976 -0.057506 -0.007102  0.013150  0.029351  0.032502  0.050503  0.029351   
1977 -0.043052 -0.035361 -0.011384 -0.004146 -0.014551 -0.032194 -0.029027   
1978 -0.006202 -0.000351  0.003699 -0.012502 -0.079557 -0.057506  0.011350   
1979  0.034302  0.052303  0.067604  0.098207  0.108558  0.082456  0.030251   

          7         8         9     ...      2990      2991      2992  \
0     0.019831  0.020283  0.036570  ... -0.051195 -0.061147 -0.065219   
1    -0.087838 -0.075171 -0.038075  ...  0.065070  0.035665 -0.002336   
2    -0.051205  0.033402  0.034752  ... -0.037254 -0.077307 -0.083158   
3     0.045165  0.022998  0.009878  ... -0.095529 -0.087838 -0.101863   
4     0.481638  0.511340  0.514041  ... -0.080908 -0.035454 -0.004401   
...        ...       ...       ...  ...       ...       ...       ...   
1975 -0.011384  0.017117  0.010783  ...  0.041546  0.001735 -0.032194   
1976  0.045103  0.082906  0.074355  ...  0.200365  0.189114  0.132410   
1977 -0.030837 -0.040790 -0.036266  ...  0.017117  0.037474  0.008069   
1978 -0.030053 -0.048955  0.048253  ...  0.033852  0.025751  0.022151   
1979  0.036102  0.032502  0.010450  ...  0.194065  0.125209  0.084706   

          2993      2994      2995      2996      2997      2998      2999  
0    -0.065671 -0.072457 -0.076529 -0.066124 -0.045766 -0.029027 -0.038528  
1    -0.024503 -0.052099 -0.042599 -0.019527 -0.012289  0.003545  0.006259  
2    -0.055256 -0.005752  0.001449 -0.024203 -0.005752 -0.037704 -0.065156  
3    -0.108648 -0.117244 -0.102315 -0.087386 -0.079695 -0.070195 -0.051647  
4    -0.003501 -0.009352  0.010450  0.022151  0.038802  0.040152  0.070305  
...        ...       ...       ...       ...       ...       ...       ...  
1975 -0.073814 -0.102315 -0.091005 -0.076076 -0.055719 -0.005955  0.046522  
1976  0.136010  0.131060  0.136010  0.144561  0.173813  0.172463  0.131510  
1977 -0.022694 -0.051647 -0.032646 -0.035361 -0.037623 -0.055719 -0.073814  
1978  0.038802  0.039252  0.010900  0.013600 -0.029603 -0.034104 -0.066056  
1979  0.076605  0.090556  0.115308  0.112158  0.166162  0.251219  0.302973  

[1980 rows x 3000 columns]

In [ ]:
x_train_with_tri_trained_labels=x_sub_set

In [ ]:
x_train_with_tri_trained_labels['pseudo_labels']=m_vote_inc

In [ ]:
x_train_with_tri_trained_labels

0         1         2         3         4         5         6  \
0     0.008521 -0.021337 -0.023599 -0.011384 -0.005051  0.006259  0.029784   
1     0.036570  0.025712  0.022093  0.026617  0.027974 -0.013194 -0.069290   
2     0.029801  0.029351  0.076605 -0.003951  0.022151  0.047353  0.165262   
3     0.047427  0.085428  0.082714  0.083166  0.094476  0.084523  0.072309   
4     0.416383  0.437534  0.459136  0.460486  0.450135  0.424033  0.438884   
...        ...       ...       ...       ...       ...       ...       ...   
1975  0.003997  0.004450  0.019831  0.028427  0.027974  0.005354 -0.015456   
1976 -0.057506 -0.007102  0.013150  0.029351  0.032502  0.050503  0.029351   
1977 -0.043052 -0.035361 -0.011384 -0.004146 -0.014551 -0.032194 -0.029027   
1978 -0.006202 -0.000351  0.003699 -0.012502 -0.079557 -0.057506  0.011350   
1979  0.034302  0.052303  0.067604  0.098207  0.108558  0.082456  0.030251   

             7         8         9  ...      2991      2992      2993  \
0     0.019831  0.020283  0.036570  ... -0.061147 -0.065219 -0.065671   
1    -0.087838 -0.075171 -0.038075  ...  0.035665 -0.002336 -0.024503   
2    -0.051205  0.033402  0.034752  ... -0.077307 -0.083158 -0.055256   
3     0.045165  0.022998  0.009878  ... -0.087838 -0.101863 -0.108648   
4     0.481638  0.511340  0.514041  ... -0.035454 -0.004401 -0.003501   
...        ...       ...       ...  ...       ...       ...       ...   
1975 -0.011384  0.017117  0.010783  ...  0.001735 -0.032194 -0.073814   
1976  0.045103  0.082906  0.074355  ...  0.189114  0.132410  0.136010   
1977 -0.030837 -0.040790 -0.036266  ...  0.037474  0.008069 -0.022694   
1978 -0.030053 -0.048955  0.048253  ...  0.025751  0.022151  0.038802   
1979  0.036102  0.032502  0.010450  ...  0.125209  0.084706  0.076605   

          2994      2995      2996      2997      2998      2999  \
0    -0.072457 -0.076529 -0.066124 -0.045766 -0.029027 -0.038528   
1    -0.052099 -0.042599 -0.019527 -0.012289  0.003545  0.006259   
2    -0.005752  0.001449 -0.024203 -0.005752 -0.037704 -0.065156   
3    -0.117244 -0.102315 -0.087386 -0.079695 -0.070195 -0.051647   
4    -0.009352  0.010450  0.022151  0.038802  0.040152  0.070305   
...        ...       ...       ...       ...       ...       ...   
1975 -0.102315 -0.091005 -0.076076 -0.055719 -0.005955  0.046522   
1976  0.131060  0.136010  0.144561  0.173813  0.172463  0.131510   
1977 -0.051647 -0.032646 -0.035361 -0.037623 -0.055719 -0.073814   
1978  0.039252  0.010900  0.013600 -0.029603 -0.034104 -0.066056   
1979  0.090556  0.115308  0.112158  0.166162  0.251219  0.302973   

      pseudo_labels  
0                 4  
1                 2  
2                 0  
3                 4  
4                 2  
...             ...  
1975              4  
1976              2  
1977              2  
1978              0  
1979              4  

[1980 rows x 3001 columns]

In [ ]:
x_train_with_tri_trained_labels.to_csv(r'/content/gdrive/My Drive/physionet/ensemble/50_subs/x_train_with_semi_sup_tri-trained_labels_frozen_layers_train_on_batch_trial_10.csv', header=False, index=False)

appending the subject specific (train data,tri-trained labels) to the (transfer set, maj_labels) 

In [ ]:
transfer_set=pd.read_csv('/content/gdrive/My Drive/physionet/ensemble/50_subs/transfer_set_50_subs.csv',header=None)

In [ ]:
sub_set_with_semi_sup_tri_trained_labels=pd.read_csv('/content/gdrive/My Drive/physionet/ensemble/50_subs/x_train_with_semi_sup_tri-trained_labels_frozen_layers_train_on_batch_trial_1.csv',header=None)

In [ ]:
transfer_set_new=transfer_set.append(sub_set_with_semi_sup_tri_trained_labels, ignore_index=True)

In [ ]:
transfer_set_new.to_csv(r'/content/gdrive/My Drive/physionet/ensemble/50_subs/transfer_set_plus_sub_dt_with_tri_trained_labels_keras_way_sub_481.csv', header=False, index=False)

In [ ]:
transfer_dt_plus_sub_dt=pd.read_csv('/content/gdrive/My Drive/physionet/ensemble/50_subs/transfer_set_plus_sub_dt_with_tri_trained_labels_keras_way_sub_481.csv',header=None)

In [ ]:
transfer_dt_plus_sub_dt

0         1         2         3         4         5         6     \
0       0.068014  0.082915  0.077628  0.074744  0.060804  0.063688  0.050710   
1       0.104729  0.054513 -0.020131 -0.064918 -0.122825 -0.127801 -0.107443   
2       0.002281 -0.031309 -0.007672 -0.020527 -0.003110 -0.011404  0.006013   
3      -0.025235 -0.037732 -0.033406 -0.031964 -0.034848 -0.041097 -0.031484   
4       0.097914 -0.100520 -0.044574 -0.079540 -0.071235 -0.029713 -0.041951   
...          ...       ...       ...       ...       ...       ...       ...   
118693  0.003997  0.004450  0.019831  0.028427  0.027974  0.005354 -0.015456   
118694 -0.057506 -0.007102  0.013150  0.029351  0.032502  0.050503  0.029351   
118695 -0.043052 -0.035361 -0.011384 -0.004146 -0.014551 -0.032194 -0.029027   
118696 -0.006202 -0.000351  0.003699 -0.012502 -0.079557 -0.057506  0.011350   
118697  0.034302  0.052303  0.067604  0.098207  0.108558  0.082456  0.030251   

            7         8         9     ...      2991      2992      2993  \
0       0.029561  0.010815  0.008412  ... -0.010334 -0.016102 -0.034368   
1      -0.086633 -0.051799 -0.033251  ... -0.123729 -0.120563 -0.129158   
2      -0.029236 -0.025089 -0.042091  ...  0.088122  0.057850  0.027992   
3      -0.025716 -0.019948 -0.030522  ... -0.015141 -0.013699 -0.018025   
4       0.000445 -0.031024  0.172217  ...  0.167409  0.220732  0.191011   
...          ...       ...       ...  ...       ...       ...       ...   
118693 -0.011384  0.017117  0.010783  ...  0.001735 -0.032194 -0.073814   
118694  0.045103  0.082906  0.074355  ...  0.189114  0.132410  0.136010   
118695 -0.030837 -0.040790 -0.036266  ...  0.037474  0.008069 -0.022694   
118696 -0.030053 -0.048955  0.048253  ...  0.025751  0.022151  0.038802   
118697  0.036102  0.032502  0.010450  ...  0.125209  0.084706  0.076605   

            2994      2995      2996      2997      2998      2999  3000  
0      -0.055998 -0.074263 -0.071860 -0.077147 -0.084838 -0.090125     4  
1      -0.149968 -0.173945 -0.187064 -0.171231 -0.149516 -0.121467     3  
2       0.038359  0.040847  0.053703  0.072779  0.055362  0.029651     2  
3      -0.020909 -0.021390 -0.002644 -0.020428 -0.025235 -0.024754     2  
4       0.119767  0.165661  0.270996  0.200190  0.246520  0.166535     0  
...          ...       ...       ...       ...       ...       ...   ...  
118693 -0.102315 -0.091005 -0.076076 -0.055719 -0.005955  0.046522     4  
118694  0.131060  0.136010  0.144561  0.173813  0.172463  0.131510     2  
118695 -0.051647 -0.032646 -0.035361 -0.037623 -0.055719 -0.073814     2  
118696  0.039252  0.010900  0.013600 -0.029603 -0.034104 -0.066056     0  
118697  0.090556  0.115308  0.112158  0.166162  0.251219  0.302973     2  

[118698 rows x 3001 columns]

In [ ]:
transfer_set

0         1         2         3         4         5         6     \
0       0.068014  0.082915  0.077628  0.074744  0.060804  0.063688  0.050710   
1       0.104729  0.054513 -0.020131 -0.064918 -0.122825 -0.127801 -0.107443   
2       0.002281 -0.031309 -0.007672 -0.020527 -0.003110 -0.011404  0.006013   
3      -0.025235 -0.037732 -0.033406 -0.031964 -0.034848 -0.041097 -0.031484   
4       0.097914 -0.100520 -0.044574 -0.079540 -0.071235 -0.029713 -0.041951   
...          ...       ...       ...       ...       ...       ...       ...   
116713  0.032558  0.033944  0.046413  0.056111  0.060267  0.066271  0.077816   
116714  0.068695  0.059483  0.051071  0.044662  0.037051  0.041057  0.040656   
116715  0.013392  0.030717  0.029805  0.016127  0.026613  0.024334  0.019775   
116716 -0.057457 -0.065629 -0.101198 -0.114176 -0.141093 -0.184354 -0.222807   
116717 -0.065742 -0.082698 -0.086365 -0.053368 -0.023122 -0.024038 -0.046494   

            7         8         9     ...      2991      2992      2993  \
0       0.029561  0.010815  0.008412  ... -0.010334 -0.016102 -0.034368   
1      -0.086633 -0.051799 -0.033251  ... -0.123729 -0.120563 -0.129158   
2      -0.029236 -0.025089 -0.042091  ...  0.088122  0.057850  0.027992   
3      -0.025716 -0.019948 -0.030522  ... -0.015141 -0.013699 -0.018025   
4       0.000445 -0.031024  0.172217  ...  0.167409  0.220732  0.191011   
...          ...       ...       ...  ...       ...       ...       ...   
116713  0.058882  0.078278  0.051493  ...  0.024707  0.025631  0.015933   
116714  0.046264  0.039054  0.045063  ...  0.035850  0.031444  0.026637   
116715  0.038012  0.027069  0.031629  ...  0.013392  0.018863  0.034820   
116716 -0.230017 -0.242514 -0.231459  ... -0.085817 -0.068993 -0.058899   
116717 -0.133109 -0.211476 -0.300383  ... -0.135401 -0.128985 -0.091864   

            2994      2995      2996      2997      2998      2999  3000  
0      -0.055998 -0.074263 -0.071860 -0.077147 -0.084838 -0.090125     4  
1      -0.149968 -0.173945 -0.187064 -0.171231 -0.149516 -0.121467     3  
2       0.038359  0.040847  0.053703  0.072779  0.055362  0.029651     2  
3      -0.020909 -0.021390 -0.002644 -0.020428 -0.025235 -0.024754     2  
4       0.119767  0.165661  0.270996  0.200190  0.246520  0.166535     0  
...          ...       ...       ...       ...       ...       ...   ...  
116713  0.044565 -0.000231  0.018242 -0.028402  0.021475  0.028402     2  
116714  0.023433  0.027839  0.023833  0.018626  0.005007  0.007010     4  
116715  0.034364  0.042115  0.045306  0.041659  0.032996  0.024334     4  
116716 -0.043999 -0.058419 -0.065629 -0.070916 -0.068513 -0.090143     2  
116717 -0.071700 -0.102404 -0.157398 -0.150524 -0.087281 -0.042828     2  

[116718 rows x 3001 columns]

trial 2,3....

In [ ]:
sub_set_with_semi_sup_tri_trained_labels=pd.read_csv('/content/gdrive/My Drive/physionet/ensemble/50_subs/x_train_with_semi_sup_tri-trained_labels_frozen_layers_train_on_batch_trial_3.csv',header=None)

In [ ]:
transfer_set_new=transfer_set.append(sub_set_with_semi_sup_tri_trained_labels, ignore_index=True)

In [ ]:
transfer_set_new.to_csv(r'/content/gdrive/My Drive/physionet/ensemble/50_subs/transfer_set_plus_sub_dt_with_tri_trained_labels_keras_way_sub_481_trial_3.csv', header=False, index=False)

In [ ]:
transfer_dt_plus_sub_dt=pd.read_csv('/content/gdrive/My Drive/physionet/ensemble/50_subs/transfer_set_plus_sub_dt_with_tri_trained_labels_keras_way_sub_481_trial_3.csv',header=None)

In [ ]:
transfer_dt_plus_sub_dt

0         1         2         3         4         5         6     \
0       0.068014  0.082915  0.077628  0.074744  0.060804  0.063688  0.050710   
1       0.104729  0.054513 -0.020131 -0.064918 -0.122825 -0.127801 -0.107443   
2       0.002281 -0.031309 -0.007672 -0.020527 -0.003110 -0.011404  0.006013   
3      -0.025235 -0.037732 -0.033406 -0.031964 -0.034848 -0.041097 -0.031484   
4       0.097914 -0.100520 -0.044574 -0.079540 -0.071235 -0.029713 -0.041951   
...          ...       ...       ...       ...       ...       ...       ...   
118693  0.003997  0.004450  0.019831  0.028427  0.027974  0.005354 -0.015456   
118694 -0.057506 -0.007102  0.013150  0.029351  0.032502  0.050503  0.029351   
118695 -0.043052 -0.035361 -0.011384 -0.004146 -0.014551 -0.032194 -0.029027   
118696 -0.006202 -0.000351  0.003699 -0.012502 -0.079557 -0.057506  0.011350   
118697  0.034302  0.052303  0.067604  0.098207  0.108558  0.082456  0.030251   

            7         8         9     ...      2991      2992      2993  \
0       0.029561  0.010815  0.008412  ... -0.010334 -0.016102 -0.034368   
1      -0.086633 -0.051799 -0.033251  ... -0.123729 -0.120563 -0.129158   
2      -0.029236 -0.025089 -0.042091  ...  0.088122  0.057850  0.027992   
3      -0.025716 -0.019948 -0.030522  ... -0.015141 -0.013699 -0.018025   
4       0.000445 -0.031024  0.172217  ...  0.167409  0.220732  0.191011   
...          ...       ...       ...  ...       ...       ...       ...   
118693 -0.011384  0.017117  0.010783  ...  0.001735 -0.032194 -0.073814   
118694  0.045103  0.082906  0.074355  ...  0.189114  0.132410  0.136010   
118695 -0.030837 -0.040790 -0.036266  ...  0.037474  0.008069 -0.022694   
118696 -0.030053 -0.048955  0.048253  ...  0.025751  0.022151  0.038802   
118697  0.036102  0.032502  0.010450  ...  0.125209  0.084706  0.076605   

            2994      2995      2996      2997      2998      2999  3000  
0      -0.055998 -0.074263 -0.071860 -0.077147 -0.084838 -0.090125     4  
1      -0.149968 -0.173945 -0.187064 -0.171231 -0.149516 -0.121467     3  
2       0.038359  0.040847  0.053703  0.072779  0.055362  0.029651     2  
3      -0.020909 -0.021390 -0.002644 -0.020428 -0.025235 -0.024754     2  
4       0.119767  0.165661  0.270996  0.200190  0.246520  0.166535     0  
...          ...       ...       ...       ...       ...       ...   ...  
118693 -0.102315 -0.091005 -0.076076 -0.055719 -0.005955  0.046522     4  
118694  0.131060  0.136010  0.144561  0.173813  0.172463  0.131510     2  
118695 -0.051647 -0.032646 -0.035361 -0.037623 -0.055719 -0.073814     2  
118696  0.039252  0.010900  0.013600 -0.029603 -0.034104 -0.066056     0  
118697  0.090556  0.115308  0.112158  0.166162  0.251219  0.302973     2  

[118698 rows x 3001 columns]

In [ ]:
transfer_set_new

0         1         2         3         4         5         6     \
0       0.068014  0.082915  0.077628  0.074744  0.060804  0.063688  0.050710   
1       0.104729  0.054513 -0.020131 -0.064918 -0.122825 -0.127801 -0.107443   
2       0.002281 -0.031309 -0.007672 -0.020527 -0.003110 -0.011404  0.006013   
3      -0.025235 -0.037732 -0.033406 -0.031964 -0.034848 -0.041097 -0.031484   
4       0.097914 -0.100520 -0.044574 -0.079540 -0.071235 -0.029713 -0.041951   
...          ...       ...       ...       ...       ...       ...       ...   
118693  0.003997  0.004450  0.019831  0.028427  0.027974  0.005354 -0.015456   
118694 -0.057506 -0.007102  0.013150  0.029351  0.032502  0.050503  0.029351   
118695 -0.043052 -0.035361 -0.011384 -0.004146 -0.014551 -0.032194 -0.029027   
118696 -0.006202 -0.000351  0.003699 -0.012502 -0.079557 -0.057506  0.011350   
118697  0.034302  0.052303  0.067604  0.098207  0.108558  0.082456  0.030251   

            7         8         9     ...      2991      2992      2993  \
0       0.029561  0.010815  0.008412  ... -0.010334 -0.016102 -0.034368   
1      -0.086633 -0.051799 -0.033251  ... -0.123729 -0.120563 -0.129158   
2      -0.029236 -0.025089 -0.042091  ...  0.088122  0.057850  0.027992   
3      -0.025716 -0.019948 -0.030522  ... -0.015141 -0.013699 -0.018025   
4       0.000445 -0.031024  0.172217  ...  0.167409  0.220732  0.191011   
...          ...       ...       ...  ...       ...       ...       ...   
118693 -0.011384  0.017117  0.010783  ...  0.001735 -0.032194 -0.073814   
118694  0.045103  0.082906  0.074355  ...  0.189114  0.132410  0.136010   
118695 -0.030837 -0.040790 -0.036266  ...  0.037474  0.008069 -0.022694   
118696 -0.030053 -0.048955  0.048253  ...  0.025751  0.022151  0.038802   
118697  0.036102  0.032502  0.010450  ...  0.125209  0.084706  0.076605   

            2994      2995      2996      2997      2998      2999  3000  
0      -0.055998 -0.074263 -0.071860 -0.077147 -0.084838 -0.090125     4  
1      -0.149968 -0.173945 -0.187064 -0.171231 -0.149516 -0.121467     3  
2       0.038359  0.040847  0.053703  0.072779  0.055362  0.029651     2  
3      -0.020909 -0.021390 -0.002644 -0.020428 -0.025235 -0.024754     2  
4       0.119767  0.165661  0.270996  0.200190  0.246520  0.166535     0  
...          ...       ...       ...       ...       ...       ...   ...  
118693 -0.102315 -0.091005 -0.076076 -0.055719 -0.005955  0.046522     4  
118694  0.131060  0.136010  0.144561  0.173813  0.172463  0.131510     2  
118695 -0.051647 -0.032646 -0.035361 -0.037623 -0.055719 -0.073814     2  
118696  0.039252  0.010900  0.013600 -0.029603 -0.034104 -0.066056     0  
118697  0.090556  0.115308  0.112158  0.166162  0.251219  0.302973     2  

[118698 rows x 3001 columns]